In [ ]:
!pip install langchain-google-genai

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 47.4/47.4 kB 3.6 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.4/1.4 MB 46.1 MB/s eta 0:00:00
  Attempting uninstall: google-ai-generativelanguage
    Found existing installation: google-ai-generativelanguage 0.6.15
    Uninstalling google-ai-generativelanguage-0.6.15:
      Successfully uninstalled google-ai-generativelanguage-0.6.15
ERROR: pip's dependency resolver does not currently take into account all the packages that are installed. This behaviour is the source of the following dependency conflicts.
google-generativeai 0.8.5 requires google-ai-generativelanguage==0.6.15, but you have google-ai-generativelanguage 0.6.18 which is incompatible.


In [ ]:
import pandas as pd
import networkx as nx
import pickle
import os
import time
from datetime import datetime
import random # For random.sample in process_article

# --- Khởi tạo các mô hình và biến toàn cục ---

# Biến toàn cục cho logic thử lại API
MAX_RETRIES = 3
BASE_DELAY = 5

# Khởi tạo các mô hình Deep Learning (NER và Sentiment Analysis)
# NER Model: NlpHUST/ner-vietnamese-electra-base
# Sentiment Model: wonrax/phobert-base-vietnamese-sentiment
try:
    from transformers import pipeline, AutoTokenizer, AutoModelForTokenClassification, AutoModelForSequenceClassification

    # NER Model
    ner_tokenizer = AutoTokenizer.from_pretrained("NlpHUST/ner-vietnamese-electra-base")
    ner_model = AutoModelForTokenClassification.from_pretrained("NlpHUST/ner-vietnamese-electra-base")
    nlp_ner_pipeline = pipeline("ner", model=ner_model, tokenizer=ner_tokenizer, aggregation_strategy="simple")
    print("Mô hình NER Deep Learning đã được khởi tạo thành công: NlpHUST/vibert-base-vietnamese-ner")

    # Sentiment Analysis Model
    sentiment_tokenizer = AutoTokenizer.from_pretrained("wonrax/phobert-base-vietnamese-sentiment")
    sentiment_model = AutoModelForSequenceClassification.from_pretrained("wonrax/phobert-base-vietnamese-sentiment")
    nlp_sentiment_pipeline = pipeline("sentiment-analysis", model=sentiment_model, tokenizer=sentiment_tokenizer)
    print("Mô hình phân loại cảm xúc Deep Learning đã được khởi tạo thành công: wonrax/phobert-base-vietnamese-sentiment")

except ImportError:
    print("Lỗi")
    exit()
except Exception as e:
    print(f"Lỗi khi khởi tạo mô hình Deep Learning: {e}")
    exit()

/usr/local/lib/python3.11/dist-packages/huggingface_hub/utils/_auth.py:94: UserWarning: 
The secret `HF_TOKEN` does not exist in your Colab secrets.
To authenticate with the Hugging Face Hub, create a token in your settings tab (https://huggingface.co/settings/tokens), set it as secret in your Google Colab and restart your session.
You will be able to reuse this secret in all of your notebooks.
Please note that authentication is recommended but still optional to access public models or datasets.
  warnings.warn(


tokenizer_config.json:   0%|          | 0.00/383 [00:00<?, ?B/s]

vocab.txt: 0.00B [00:00, ?B/s]

tokenizer.json: 0.00B [00:00, ?B/s]

special_tokens_map.json:   0%|          | 0.00/125 [00:00<?, ?B/s]

...

config.json:   0%|          | 0.00/999 [00:00<?, ?B/s]

pytorch_model.bin:   0%|          | 0.00/540M [00:00<?, ?B/s]

model.safetensors:   0%|          | 0.00/540M [00:00<?, ?B/s]

Device set to use cpu


Mô hình phân loại cảm xúc Deep Learning đã được khởi tạo thành công: wonrax/phobert-base-vietnamese-sentiment


In [ ]:
from google.api_core.exceptions import TooManyRequests


In [ ]:
from concurrent.futures import ThreadPoolExecutor

In [ ]:
# Khởi tạo mô hình LLM cho trích xuất mối quan hệ (Phase 2) VÀ fallback (Phase 1)
try:
    from langchain_google_genai import ChatGoogleGenerativeAI
    from langchain_core.prompts import PromptTemplate

    # --- Cung cấp API Key cho Gemini và đặt vào biến môi trường ---
    API_KEY = ""

    if not API_KEY or API_KEY == " ":
        print("Lỗi")
        exit() # Dừng chương trình nếu API Key chưa được cung cấp

    os.environ["GOOGLE_API_KEY"] = API_KEY # Đặt API Key vào biến môi trường

    model_llm = ChatGoogleGenerativeAI(model="gemini-2.0-flash", temperature=0.1)
    # Thư viện sẽ tự động lấy từ biến môi trường GOOGLE_API_KEY

    # --- ĐỊNH NGHĨA LẠI entity_extraction_template VÀ chain_entity CHO FALLBACK ---
    entity_extraction_template = PromptTemplate.from_template("""Bạn đang làm việc dưới bối cảnh phân tích kinh tế.
Bạn được cho một hoặc nhiều bài báo, bao gồm tựa đề và mô tả ngắn gọn về bài báo đó, ngoài ra bạn có
thông tin về ngày xuất bản của bài báo, và loại chủ đề mà bài báo đang đề cập tới.

Hạn chế tạo mới một thực thể, chỉ tạo liên kết tới 5 thực thể. Luôn ưu tiên liên kết với các thực thể đã có: {existing_entities}

Bạn cần phân tích bài báo, đưa ra tên của những thực thể (ví dụ như cổ phiếu, ngành nghề, công ty, quốc gia, tỉnh thành...)
sẽ bị ảnh hưởng trực tiếp bởi thông tin của bài báo, theo hướng tích cực hoặc tiêu cực.

Với mỗi thực thể, ở phần Tên thực thể, hạn chế dùng dấu chấm, gạch ngang, dấu và &, dấu chấm phẩy ;. Và cần ghi thêm quốc gia, địa phương cụ thể và ngành nghề của nó (nếu có).
Tên chỉ nói tới một thực thể duy nhất. Phần Tên không được quá phức tạp, đơn giản nhất có thể.
Nếu thực thể nào thuộc danh mục cổ phiếu sau: {portfolio}, hãy ghi rõ tên cổ phiếu.
Ví dụ: SSI-Chứng khoán; Ngành công nghiệp Việt Nam; Người dùng Mỹ; Ngành thép Châu Á; Ngành du lịch Hạ Long, ...

Ghi nhớ, Hạn chế tạo mới một thực thể, chỉ tạo liên kết tới 5 thực thể. Luôn cố liên kết với các thực thể đã có.

Phần giải thích mỗi thực thể, bắt buộc đánh giá số liệu được ghi, nhiều hoặc ít, tăng hoặc giảm, gấp bao nhiêu lần, ...
Cần cố gắng liên kết với nhiều thực thể khác. Tuy nhiên không suy ngoài phạm vi bài báo. Không tự chèn số liệu ngoài bài báo.
Không dùng dấu hai chấm trong phần giải thích, chỉ dùng hai chấm : để tách giữa Tên thực thể và phần giải thích.

Đưa ra theo định dạng sau:
[[POSITIVE]]
[Entity 1]: [Explanation]
...
[Entity N]: [Explanation]

[[NEGATIVE]]
[Entity A]: [Explanation]
..
[Entity Z]: [Explanation]

Một ví dụ cho bài báo:

(BẮT ĐẦU VÍ DỤ)

Ngày đăng: 2025-04-07T22:51:00+07:00
Loại chủ đề: Kinh tế
Tựa đề: Nỗ lực hiện thực hóa mục tiêu thông tuyến cao tốc từ Cao Bằng đến Cà Mau

Mô tả: Nhằm hoàn thành mục tiêu đến năm 2025 cả nước có trên 3.000 km đường cao tốc, Bộ Xây dựng, các địa phương và doanh nghiệp đang triển khai thi công 28 dự án/dự án thành phần với tổng chiều dài khoảng 1.188 km.
Đến nay, tiến độ đa số các dự án bám sát kế hoạch, nhiều dự án đăng ký hoàn thành thông tuyến trong năm 2025. Có thể nói ngành giao thông vận tải đang cố gắng hết sức.

Danh sách thực thể sẽ bị ảnh hưởng:

[[POSITIVE]]
Bộ Xây dựng Việt Nam: Áp lực quản lý 28 dự án với tổng chiều dài 1188 km, nhằm hiện thực hóa mục tiêu đạt 3000 km cao tốc vào năm 2025. Số lượng dự án tăng gấp nhiều lần so với giai đoạn trước, đòi hỏi điều phối nguồn lực và kiểm soát tiến độ chặt chẽ hơn.
Chính quyền địa phương Việt Nam: Trực tiếp phối hợp triển khai các dự án tại từng tỉnh thành. Cần nâng cao năng lực quản lý và sử dụng ngân sách công hiệu quả để đảm bảo tiến độ thi công theo kế hoạch chung quốc gia.
Doanh nghiệp xây dựng Việt Nam: Được hưởng lợi trực tiếp khi nhận khối lượng hợp đồng thi công lớn. Doanh thu và năng lực thi công có thể tăng nhanh hơn so với các giai đoạn trước đây, nhờ nhu cầu đầu tư hạ tầng tăng mạnh.
Ngành giao thông vận tải Việt Nam: Cải thiện hạ tầng cao tốc giúp rút ngắn thời gian di chuyển liên vùng, từ đó nâng cao hiệu suất vận hành và giảm chi phí logistics trên toàn quốc.
Tỉnh Cao Bằng Việt Nam: Là điểm đầu của tuyến cao tốc quốc gia, đóng vai trò đầu mối kết nối vùng Đông Bắc. Hạ tầng mới giúp tăng kết nối, tạo cơ hội thu hút đầu tư và đẩy nhanh tốc độ phát triển kinh tế địa phương.
Tỉnh Cà Mau Việt Nam: Là điểm cuối của tuyến cao tốc, với hệ thống giao thông hiện đại giúp mở rộng thị trường du lịch và phát triển kinh tế vùng Đồng bằng sông Cửu Long. Tạo lợi thế cạnh tranh mới cho địa phương.

[[NEGATIVE]]
Bộ Xây dựng Việt Nam: Rủi ro chậm tiến độ và đội vốn nếu điều phối không hiệu quả do số lượng dự án tăng gấp nhiều lần.
Chính quyền địa phương Việt Nam: Có thể gặp khó khăn trong giải phóng mặt bằng và quản lý vốn đầu tư nếu năng lực tổ chức yếu.
Doanh nghiệp xây dựng Việt Nam: Thi công đồng loạt nhiều dự án có thể làm giãn mỏng năng lực nhân sự và máy móc tăng rủi ro chậm tiến độ hoặc giảm chất lượng.
Doanh nghiệp ngoài ngành xây dựng Việt Nam: Chịu tác động gián tiếp từ chi phí logistics tăng tạm thời hoặc thiếu hụt nguyên vật liệu.

(KẾT THÚC VÍ DỤ)

Ngày đăng: {date}
Loại chủ đề: {group}
Tựa đề: {title}

Mô tả: {description}


Danh sách thực thể sẽ bị ảnh hưởng:
""")
    chain_entity = entity_extraction_template | model_llm # Sử dụng model_llm cho chain_entity

    # Định nghĩa PromptTemplate cho trích xuất mối quan hệ theo lô (batch_relation_extraction_template)
    batch_relation_extraction_template = PromptTemplate.from_template("""
    Bạn là một chuyên gia phân tích kinh tế. Bạn được cung cấp một danh sách các thực thể gốc đã được trích xuất từ một bài báo, cùng với ảnh hưởng và nội dung liên quan của chúng.
    Nhiệm vụ của bạn là xác định các mối quan hệ giữa các thực thể này và các thực thể khác (nếu có), đồng thời chỉ ra ảnh hưởng (POSITIVE/NEGATIVE) của mối quan hệ đó.

    Hạn chế tạo mới thực thể, chỉ tạo liên kết tới tối đa 5 thực thể cho mỗi thực thể gốc. Luôn ưu tiên liên kết với các thực thể đã có trong đồ thị: {existing_entities}
    Nếu một thực thể thuộc danh mục cổ phiếu sau: {portfolio}, hãy ghi rõ tên cổ phiếu.

    Đưa ra theo định dạng sau:
    [[SOURCE: [Tên Thực thể Gốc]]]
    [[IMPACT: [POSITIVE/NEGATIVE]]]
    [[POSITIVE]]
    [Thực thể Đích 1]: [Giải thích mối quan hệ]
    ...
    [[NEGATIVE]]
    [Thực thể Đích A]: [Giải thích mối quan hệ]
    ...

    Nếu không có mối quan hệ nào được tìm thấy cho một thực thể gốc, không cần liệt kê phần đó.
    Không dùng dấu hai chấm trong phần giải thích, chỉ dùng hai chấm : để tách giữa Tên thực thể và phần giải thích.

    Ví dụ:
    [[SOURCE: Ngân hàng VPBank]]
    [[IMPACT: POSITIVE]]
    [[POSITIVE]]
    Cổ phiếu VPB: Giá cổ phiếu tăng 5% sau thông tin lợi nhuận quý 1 vượt trội.
    Ngành Ngân hàng Việt Nam: Lợi nhuận tăng trưởng mạnh mẽ, cho thấy sự phục hồi của toàn ngành.

    [[SOURCE: Giá dầu thô]]
    [[IMPACT: NEGATIVE]]
    [[NEGATIVE]]
    Ngành Vận tải Việt Nam: Chi phí nhiên liệu tăng cao, ảnh hưởng đến lợi nhuận.
    Người tiêu dùng Việt Nam: Giá xăng dầu tăng, giảm sức mua.

    Các thực thể gốc cần phân tích:
    {input_entities}
    """)
    chain_batch_relation = batch_relation_extraction_template | model_llm
    print("Mô hình LLM cho trích xuất mối quan hệ đã được khởi tạo thành công.")

except ImportError:
    print("Lỗi thư viện 'langchain-google-genai'")
    exit()
except Exception as e:
    print(f"Lỗi khi khởi tạo mô hình LLM: {e}")


Mô hình LLM cho trích xuất mối quan hệ đã được khởi tạo thành công.


In [ ]:
# --- Các hàm hỗ trợ ---
def graph_entities_to_str(G):
    """
    Lấy chuỗi các nút loại "entity" từ đồ thị để làm ngữ cảnh cho LLM.
    """
    entities = [node for node in G.nodes() if G.nodes[node].get("type") == "entity"]
    graph_str = ", ".join(entities)
    return graph_str[:20000] if len(graph_str) > 20000 else graph_str

import re
from google.api_core.exceptions import ResourceExhausted

def invoke_chain_with_retry(chain, prompt, max_retries=MAX_RETRIES, base_delay=BASE_DELAY):
    retry_count = 0
    while True:
        try:
            response = chain.invoke(prompt)
            time.sleep(5)  # Độ trễ cố định
            return response
        except ResourceExhausted as e:
            retry_count += 1
            if retry_count > max_retries:
                print(f"Đã đạt số lần thử lại tối đa. Lỗi: {e}")
                return None
            # Tìm retry_delay trong chuỗi lỗi
            retry_after = base_delay
            error_str = str(e)
            match = re.search(r'retry_delay\s*\{\s*seconds:\s*(\d+)\s*\}', error_str)
            if match:
                retry_after = float(match.group(1))
            delay = retry_after + random.uniform(0, 1)  # Thêm jitter
            print(f"Lỗi 429: Thử lại sau {delay} giây... (Lần thử {retry_count}/{max_retries})")
            time.sleep(delay)
        except Exception as e:
            retry_count += 1
            if retry_count > max_retries:
                print(f"Đã đạt số lần thử lại tối đa. Lỗi: {e}")
                return None
            delay = base_delay * (2 ** (retry_count - 1))
            print(f"Lỗi: {e}. Thử lại sau {delay} giây... (Lần thử {retry_count}/{max_retries})")
            time.sleep(delay)
def parse_entity_response(response):
    """
    Parses the response from the entity extraction prompt (LLM fallback).
    """
    if response is None:
        print("Phản hồi LLM là None.")
        return {"POSITIVE": [], "NEGATIVE": []}

    sections = {"POSITIVE": [], "NEGATIVE": []}
    current_section = None
    str_resp = response.content # Sử dụng .content cho đối tượng response từ LangChain

    for line in str(str_resp).splitlines():
        line = line.strip()
        if not line:
            continue
        if "[[POSITIVE]]" in line.upper():
            current_section = "POSITIVE"
            continue
        if "[[NEGATIVE]]" in line.upper():
            current_section = "NEGATIVE"
            continue
        if current_section and ':' in line:
            entity = line.split(":", 1)[0].strip()
            if not entity or "không có thực thể nào" in entity.lower():
                continue
            content = line.split(entity, 1)[-1].strip(':').strip()
            sections[current_section].append((entity, content))

    return sections

def parse_batch_entity_response(response):
    """
    Phân tích phản hồi từ prompt trích xuất mối quan hệ theo lô.
    Trả về danh sách các tuple (source_entity, impact, target_entity, content).
    """
    if response is None:
        print("Phản hồi là None.")
        return []

    results = []
    current_source = None
    current_impact = None
    current_section = None

    str_resp = str(response.content)
    lines = str_resp.splitlines()

    for line in lines:
        line = line.strip()
        if not line:
            continue

        if line.startswith("[[SOURCE:") or "[[SOURCE:" in line:
            source_text = line.replace("[[SOURCE:", "").replace("]]", "").strip()
            if source_text and "không có thực thể nào" not in source_text.lower():
                current_source = source_text
            else:
                current_source = None
            current_impact = None # Reset impact for new source
            current_section = None # Reset section for new source
            continue

        if line.startswith("[[IMPACT:") or "[[IMPACT:" in line:
            impact_str = line.replace("[[IMPACT:", "").replace("]]", "").strip()
            current_impact = impact_str.upper()
            continue

        if "[[POSITIVE]]" in line.upper():
            current_section = "POSITIVE"
            continue

        if "[[NEGATIVE]]" in line.upper():
            current_section = "NEGATIVE"
            continue

        if current_source and current_section and ':' in line:
            try:
                entity, *content_parts = line.split(":", 1)
                entity = entity.strip().strip('[]')

                if not entity or "không có thực thể nào" in entity.lower():
                    continue

                if entity and content_parts:
                    content = content_parts[0].strip()
                    actual_impact = current_impact if current_impact else current_section
                    results.append((current_source, actual_impact, entity, content))
            except Exception as e:
                print(f"Lỗi phân tích dòng: {line}. Lỗi: {e}")
                continue

    if not results:
        print("Cảnh báo: Không có mối quan hệ nào được phân tích từ phản hồi.")
        print(f"Nội dung phản hồi: {str_resp[:500]}...")

    return results

def merge_entity(entity, canonical_set):
    """
    Trả về phiên bản chuẩn hóa của thực thể nếu đã có (không phân biệt chữ hoa/thường),
    nếu không thì thêm và trả về thực thể mới.
    """
    normalized_entity = str(entity).strip('[').strip(']').strip(' ').lower()
    for exist in canonical_set:
        if exist.lower() == normalized_entity:
            return exist
    canonical_set.add(normalized_entity)
    return normalized_entity

def add_edge(G, source, target, impact, timestamp):
    """
    Thêm một cạnh vào đồ thị nếu nó chưa tồn tại.
    """
    if not G.has_edge(source, target):
        G.add_edge(source, target, impact=impact, timestamp=timestamp)

# --- Hàm trích xuất thực thể thô bằng Deep Learning ---
def extract_entities_with_dl_model(text):
    """
    Sử dụng mô hình Deep Learning NER để trích xuất TÊN THỰC THỂ.
    Trả về danh sách các thực thể thô được trích xuất.
    """
    extracted_data = []
    try:
        ner_results = nlp_ner_pipeline(text)

        for ent_info in ner_results:
            entity_name = ent_info['word'].strip()
            # Lọc các thực thể có độ tin cậy thấp hoặc quá ngắn
            if entity_name and len(entity_name) > 1 and ent_info.get('score', 0) > 0.7:
                extracted_data.append(entity_name)

        return extracted_data
    except Exception as e:
        print(f"Lỗi khi gọi mô hình Deep Learning NER: {e}")
        return []

# --- Hàm xác định tác động (Impact) bằng mô hình phân loại cảm xúc nhỏ ---
def determine_impact_by_sentiment_model(text_to_analyze):
    """
    Sử dụng mô hình phân loại cảm xúc để gán tác động (POSITIVE/NEGATIVE).
    """
    try:
        sentiment_result = nlp_sentiment_pipeline(text_to_analyze)

        if sentiment_result and len(sentiment_result) > 0:
            label = sentiment_result[0]['label']
            score = sentiment_result[0]['score']

            if label == "LABEL_1" and score > 0.7:
                return "POSITIVE"
            elif label == "LABEL_0" and score > 0.7:
                return "NEGATIVE"

        return "POSITIVE" # Mặc định là tích cực nếu không rõ ràng hoặc độ tin cậy thấp
    except Exception as e:
        print(f"Lỗi khi gọi mô hình phân loại cảm xúc: {e}")
        return "POSITIVE" # Fallback nếu có lỗi
def batch_process_entity_relationships(entity_batch, G, canonical_entities, portfolio, portfolio_str_full, article_timestamp):
    """
    Process multiple entities in a single API call
    Returns a list of new entities to process
    """
    if not entity_batch:
        return []

    # Maximum retries for batch processing
    max_batch_retries = 2
    batch_retry_count = 0
    relationships = []

    while batch_retry_count < max_batch_retries:
        # Format the input entities for the prompt more explicitly
        input_entities_text = ""
        for entity, impact, content in entity_batch:
            # Format similar to the relation_extraction_template structure
            input_entities_text += f"Thực thể gốc: {entity}\n\nẢnh hưởng: {impact}, {content}\n\n---\n\n"

        # Create prompt for batch relation extraction
        prompt_batch = {
            "input_entities": input_entities_text,
            "portfolio": portfolio_str_full,
            "existing_entities": graph_entities_to_str(G)
        }

        # Get relationships with retry logic
        response = invoke_chain_with_retry(chain_batch_relation, prompt_batch)
        time.sleep(10)  # Rate limiting

        if response is None:
            return []

        # Parse the response to get all relationships
        relationships = parse_batch_entity_response(response)

        # Check if we got any relationships
        if len(relationships) > 0:
            break

        batch_retry_count += 1
        print(f"Batch processing returned 0 relationships. Retry {batch_retry_count}/{max_batch_retries}")
        time.sleep(BASE_DELAY)  # Wait before retrying
        # Debug print
    print(f"Processing batch with {len(relationships)} relationships using timestamp: {article_timestamp}")

    # Process the relationships to update the graph and collect new entities
    next_entities = []

    for source, impact, target, content in relationships:
        # Skip invalid relationships
        if "không có thực thể nào" in source.lower() or "không có thực thể nào" in target.lower():
            continue

        canon_source = source  # Source entity should already be canonical
        canon_target = merge_entity(target, canonical_entities)

        # Determine if target is a stock
        node_type = "stock" if any(str(canon_target).lower().find(stock.lower()) != -1 for stock in portfolio) else "entity"

        # Add node if it doesn't exist
        if not G.has_node(canon_target):
            G.add_node(canon_target, type=node_type, timestamp=article_timestamp)

        # Add edge from source to target, ensuring we use the article timestamp
        add_edge(G, canon_source, canon_target, impact, article_timestamp)

        # Add to frontier if it's an entity (not a stock)
        if node_type == "entity":
            next_entities.append((canon_target, impact, content))

    return next_entities
# --- Hàm process_article được điều chỉnh ---
def process_article(idx, row, G, canonical_entities, portfolio, portfolio_sector, max_frontier_size=5):
    """
    Xử lý một bài báo để trích xuất thực thể và xây dựng mối quan hệ.
    Sử dụng mô hình Deep Learning cho trích xuất thực thể ban đầu và phân loại cảm xúc cho tác động,
    với fallback về LLM nếu DL không thành công.
    """
    portfolio_str_full = ", ".join([f"{stock}-{sector}" for stock, sector in zip(portfolio, portfolio_sector)])
    article_node = f"Article_{idx}: {row['title']}"
    article_timestamp = row['parsed_date']

    if not G.has_node(article_node):
        G.add_node(article_node, type="article", timestamp=article_timestamp)

    new_nodes = 0
    new_edges = 0

    use_llm_fallback = False # Cờ để kiểm soát việc fallback về LLM

    # --- GIAI ĐOẠN 1: TRÍCH XUẤT THỰC THỂ BAN ĐẦU BẰNG DEEP LEARNING ---
    article_full_text = f"Tiêu đề: {row['title']}. Mô tả: {row['description']}"

    # Bước 1.1: Trích xuất tên thực thể bằng mô hình Deep Learning NER
    raw_dl_entities = extract_entities_with_dl_model(article_full_text)

    if not raw_dl_entities: # Nếu NER không trích xuất được thực thể nào
        print(f"Bài báo {idx}: NER không trích xuất được thực thể. Đang chuyển sang LLM fallback.")
        use_llm_fallback = True

    entities_with_impact = {"POSITIVE": [], "NEGATIVE": []}

    if not use_llm_fallback: # Chỉ thực hiện nếu NER thành công
        # Bước 1.2: Gán tác động (impact) cho từng thực thể đã trích xuất bằng mô hình Sentiment Analysis
        for ent_name in raw_dl_entities:
            impact = determine_impact_by_sentiment_model(row['description'])
            ent_content_summary = row['description'] # Sử dụng mô tả làm nội dung giải thích ban đầu

            if impact == "POSITIVE":
                entities_with_impact["POSITIVE"].append((ent_name, ent_content_summary))
            elif impact == "NEGATIVE":
                entities_with_impact["NEGATIVE"].append((ent_name, ent_content_summary))

        # Kiểm tra lại sau khi gán impact, nếu không có thực thể nào có impact hợp lệ
        if not (entities_with_impact["POSITIVE"] or entities_with_impact["NEGATIVE"]):
            print(f"Bài báo {idx}: SA không gán được tác động hợp lệ cho thực thể DL. Đang chuyển sang LLM fallback.")
            use_llm_fallback = True

    # --- FALLBACK VỀ LLM NẾU CÁC MÔ HÌNH DL KHÔNG THÀNH CÔNG ---
    if use_llm_fallback:
        prompt_text = {
            "portfolio": portfolio_str_full,
            "date": row['date'],
            "group": row['group'],
            "title": row['title'],
            "description": row['description'],
            "existing_entities": graph_entities_to_str(G)
        }

        response_text = invoke_chain_with_retry(chain_entity, prompt_text)
        # time.sleep(1) # Đã chuyển sleep vào invoke_chain_with_retry

        if response_text is None:
            print(f"Bỏ qua bài báo {idx} do lỗi API LLM (fallback).")
            return 0, 0

        entities_dict_from_llm = parse_entity_response(response_text)

        # Gán kết quả từ LLM cho entities_with_impact để xử lý tiếp
        entities_with_impact = entities_dict_from_llm
        print(f"Bài báo {idx}: Đã sử dụng LLM fallback để trích xuất thực thể.")

    total_entities = len(entities_with_impact.get("POSITIVE", [])) + len(entities_with_impact.get("NEGATIVE", []))
    if total_entities == 0:
        print(f"Không thể trích xuất hoặc gán tác động cho thực thể từ bài báo {idx} sau cả DL và LLM fallback.")
        return 0, 0

    # Tiếp tục xử lý các thực thể đã có impact (Logic giống hệt như trước)
    initial_entities = []
    for impact_type in ["POSITIVE", "NEGATIVE"]:
        for ent, content in entities_with_impact.get(impact_type, []):
            if not ent or "không có thực thể nào" in ent.lower():
                continue

            canon_ent = merge_entity(ent, canonical_entities)
            node_type = "stock" if any(str(canon_ent).lower().find(stock.lower()) != -1 for stock in portfolio) else "entity"

            if not G.has_node(canon_ent):
                G.add_node(canon_ent, type=node_type, timestamp=article_timestamp)
                new_nodes += 1

            if node_type == "entity":
                initial_entities.append((canon_ent, impact_type, content))

            add_edge(G, article_node, canon_ent, impact_type, article_timestamp)
            new_edges += 1

    print(f"Chỉ số: {idx}, thực thể ban đầu (Tổng hợp): {len(initial_entities)}")

    # --- GIAI ĐOẠN 2: Mở rộng Mối quan hệ (Vẫn dùng LLM - chain_batch_relation) ---
    frontier = initial_entities
    iter_count = 0
    MAX_ITER = 2 # Số lần lặp tối đa cho mở rộng frontier

    while frontier and iter_count < MAX_ITER:
        if len(frontier) > max_frontier_size:
            frontier = random.sample(frontier, max_frontier_size)
            print(f"Chỉ số: {idx}, giới hạn frontier xuống {max_frontier_size} thực thể")

        next_frontier = batch_process_entity_relationships(
            frontier, G, canonical_entities, portfolio, portfolio_str_full, article_timestamp
        )

        # Loại bỏ trùng lặp bằng tên thực thể
        frontier = list({ent: (ent, imp, txt) for ent, imp, txt in next_frontier}.values())
        if len(frontier) > max_frontier_size:
            frontier = random.sample(frontier, max_frontier_size)

        print(f"Chỉ số: {idx}, frontier tiếp theo: {len(frontier)}")
        iter_count += 1

    return new_nodes, new_edges

In [ ]:
# --- Hàm chính để xây dựng đồ thị tri thức ---
def build_knowledge_graph(df, portfolio, portfolio_sector, skip=0, use_threading=True, max_frontier_size=5, max_workers=2,
                          graph_checkpoint=None, canonical_checkpoint=None, start_date=None, end_date=None):
    """
    Xây dựng đồ thị tri thức từ các bài báo với xử lý theo lô được tối ưu hóa.
    Xử lý nhiều bài báo song song bằng cách sử dụng luồng.
    Cho phép lọc bài báo theo ngày.
    Nếu file knowledge_graph_p3.pkl tồn tại, sẽ load và thêm vào đồ thị hiện có.
    Nếu không, sẽ tạo mới và lưu.
    """
    G = nx.DiGraph()
    canonical_entities = set()

    final_graph_output_file = "/content/merged_knowledge_graph_0104.pkl"
    final_canonical_output_file = "/content/merged_canonical_set_0104.pkl"

    # --- Sửa đổi chính ở đây: Kiểm tra và tải đồ thị/thực thể cuối cùng trước tiên ---
    if os.path.exists(final_graph_output_file):
        print(f"Đang tải đồ thị tri thức từ file cuối cùng: {final_graph_output_file}")
        try:
            with open(final_graph_output_file, "rb") as f:
                G = pickle.load(f)
            print(f"Đã tải đồ thị với {G.number_of_nodes()} nút và {G.number_of_edges()} cạnh từ file cuối cùng.")
        except Exception as e:
            print(f"Lỗi khi tải đồ thị từ file cuối cùng '{final_graph_output_file}': {e}")
            print("Bắt đầu với đồ thị rỗng.")
            G = nx.DiGraph() # Đảm bảo G là đồ thị rỗng nếu lỗi

    if os.path.exists(final_canonical_output_file):
        print(f"Đang tải các thực thể chuẩn hóa từ file cuối cùng: {final_canonical_output_file}")
        try:
            with open(final_canonical_output_file, "rb") as f:
                canonical_entities = pickle.load(f)
            print(f"Đã tải {len(canonical_entities)} thực thể chuẩn hóa từ file cuối cùng.")
        except Exception as e:
            print(f"Lỗi khi tải thực thể chuẩn hóa từ file cuối cùng '{final_canonical_output_file}': {e}")
            print("Bắt đầu với tập hợp thực thể chuẩn hóa rỗng.")
            canonical_entities = set() # Đảm bảo canonical_entities là tập hợp rỗng nếu lỗi
    # --- Kết thúc sửa đổi chính ---
    if graph_checkpoint and os.path.exists(graph_checkpoint) and not os.path.exists(final_graph_output_file):
        print(f"Đang tải đồ thị tri thức từ checkpoint: {graph_checkpoint}")
        try:
            with open(graph_checkpoint, "rb") as f:
                # Nếu đã tải G từ file cuối cùng, không ghi đè từ checkpoint
                # Nếu không, G sẽ vẫn là đồ thị rỗng ban đầu, và chúng ta tải từ checkpoint
                temp_G = pickle.load(f)
                G.add_nodes_from(temp_G.nodes(data=True))
                G.add_edges_from(temp_G.edges(data=True))
            print(f"Đã thêm đồ thị từ checkpoint với {temp_G.number_of_nodes()} nút và {temp_G.number_of_edges()} cạnh vào đồ thị hiện có.")
        except Exception as e:
            print(f"Lỗi khi tải checkpoint đồ thị: {e}")
            print("Bắt đầu với đồ thị rỗng.")

    if canonical_checkpoint and os.path.exists(canonical_checkpoint) and not os.path.exists(final_canonical_output_file):
        print(f"Đang tải các thực thể chuẩn hóa từ checkpoint: {canonical_checkpoint}")
        try:
            temp_canonical_entities = set()
            with open(canonical_checkpoint, "rb") as f:
                temp_canonical_entities = pickle.load(f)
            canonical_entities.update(temp_canonical_entities) # Hợp nhất các thực thể
            print(f"Đã thêm {len(temp_canonical_entities)} thực thể chuẩn hóa từ checkpoint vào tập hợp hiện có.")
        except Exception as e:
            print(f"Lỗi khi tải checkpoint thực thể chuẩn hóa: {e}")
            print("Bắt đầu với tập hợp thực thể chuẩn hóa rỗng.")


    df['parsed_date'] = pd.to_datetime(df['date'], utc=True)

    if start_date:
        start_filter_dt = pd.to_datetime(start_date, utc=True)
        df = df[df['parsed_date'] >= start_filter_dt]
        print(f"Đã lọc bài báo từ ngày: {start_date}")
    if end_date:
        end_filter_dt = pd.to_datetime(end_date, utc=True)
        df = df[df['parsed_date'] <= end_filter_dt]
        print(f"Đã lọc bài báo đến ngày: {end_date}")

    if skip > 0:
        print(f"Bỏ qua {skip} bài báo đầu tiên")
        df = df.iloc[skip:]

    if df.empty:
        print("DataFrame rỗng sau khi lọc. Không có bài báo nào để xử lý.")
        # Lưu đồ thị hiện có (nếu có) trước khi thoát
        try:
            with open(final_graph_output_file, "wb") as f:
                pickle.dump(G, f)
            with open(final_canonical_output_file, "wb") as f:
                pickle.dump(canonical_entities, f)
            print(f"Đồ thị cuối cùng và tập hợp thực thể đã được lưu (không có bài báo mới được xử lý).")
        except Exception as e:
            print(f"Cảnh báo: Lỗi khi lưu đồ thị/thực thể khi DataFrame rỗng: {e}")
        return G

    chunk_size = 10

    for chunk_start in range(0, len(df), chunk_size):
        chunk_end = min(chunk_start + chunk_size, len(df))
        chunk_df = df.iloc[chunk_start:chunk_end]

        postid_start = chunk_df['postID'].iloc[0]
        postid_end = chunk_df['postID'].iloc[-1]
        print(f"\nĐang xử lý bài báo từ postID {postid_start} đến {postid_end}")

        if use_threading and len(chunk_df) > 1:
            articles_processed = 0
            with ThreadPoolExecutor(max_workers=min(max_workers, len(chunk_df))) as executor:
                futures = [
                    executor.submit(
                        process_article,
                        idx,
                        row,
                        G, # Truyền G trực tiếp để các luồng có thể sửa đổi nó
                        canonical_entities, # Truyền canonical_entities trực tiếp
                        portfolio,
                        portfolio_sector,
                        max_frontier_size
                    )
                    for idx, row in chunk_df.iterrows()
                ]

                for future in futures:

                    future.result() # Đảm bảo chờ kết quả để bắt exception nếu có
                    articles_processed += 1

            print(f"Đã xử lý {articles_processed} bài báo song song")
        else:
            for idx, row in chunk_df.iterrows():
                process_article(
                    idx,
                    row,
                    G,
                    canonical_entities,
                    portfolio,
                    portfolio_sector,
                    max_frontier_size
                )

        # Lưu checkpoint sau mỗi chunk (đảm bảo thư mục tồn tại)
        checkpoint_dir = "checkpoints" # Thư mục con để lưu checkpoints
        os.makedirs(checkpoint_dir, exist_ok=True) # Tạo thư mục checkpoints nếu chưa tồn tại

        checkpoint_file = os.path.join(checkpoint_dir, f"knowledge_graph_p3_checkpoint_{postid_end}.pkl")
        with open(checkpoint_file, "wb") as f:
            pickle.dump(G, f)

        canonical_set_file = os.path.join(checkpoint_dir, f"canonical_set_checkpoint_{postid_end}.pkl")
        with open(canonical_set_file, "wb") as f:
            pickle.dump(canonical_entities, f)

        print(f"Đã lưu checkpoint sau khi xử lý postID đến {postid_end}")
        print(f"Đồ thị hiện có {G.number_of_nodes()} nút và {G.number_of_edges()} cạnh")

    # Lưu đồ thị cuối cùng
    try:
        with open(final_graph_output_file, "wb") as f:
            pickle.dump(G, f)
        with open(final_canonical_output_file, "wb") as f:
            pickle.dump(canonical_entities, f)
        print(f"\nHoàn thành xây dựng đồ thị. Đồ thị cuối cùng đã được lưu vào '{final_graph_output_file}' và '{final_canonical_output_file}'.")
    except Exception as e:
        print(f"Lỗi khi lưu đồ thị/thực thể cuối cùng: {e}")

    print(f"\nHoàn thành xây dựng đồ thị với {G.number_of_nodes()} nút và {G.number_of_edges()} cạnh")
    return G

In [ ]:
try:
    df_articles = pd.read_csv('/content/summarized_articles.csv')
    df_articles['date'] = pd.to_datetime(df_articles['date'])
    print("Đã tải file CSV thành công.")
except FileNotFoundError:
    print("Không tìm thấy file 'your_articles.csv'. Đang sử dụng DataFrame giả lập.")
except Exception as e:
    print(f"Lỗi khi đọc file CSV: {e}. Đang sử dụng DataFrame giả lập.")

Đã tải file CSV thành công.


In [ ]:
if __name__ == "__main__":

    # Danh mục cổ phiếu và lĩnh vực (ví dụ)
    my_portfolio = ["FPT", "SSI", "VCB", "VHM", "HPG", "GAS", "MSN", "MWG", "GVR", "VCG"]
    my_portfolio_sector = ["Công nghệ", "Chứng khoán", "Ngân hàng", "Bất động sản", "Vật liệu cơ bản", "Dịch vụ Hạ tầng", "Tiêu dùng cơ bản", "Bán lẻ", "Chế biến", "Công nghiệp"]

    # --- Gọi hàm xây dựng đồ thị với lọc theo ngày ---
    # Chỉ định ngày bắt đầu và kết thúc để lọc bài báo
    # Định dạng YYYY-MM-DD
    start_filter_date = "2025-03-08"
    end_filter_date = "2025-03-09"

    print(f"\nBắt đầu xây dựng đồ thị cho các bài báo từ {start_filter_date} đến {end_filter_date}")
    final_graph = build_knowledge_graph(
        df=df_articles,
        portfolio=my_portfolio,
        portfolio_sector=my_portfolio_sector,
        skip=0,
        use_threading=False,  # Tắt xử lý song song
        max_frontier_size=5,
        max_workers=5,
        graph_checkpoint="knowledge_graph_p3_checkpoint_100.pkl",
        canonical_checkpoint="canonical_set_checkpoint_100.pkl",
        start_date=start_filter_date,
        end_date=end_filter_date
    )

    print("\n--- Xây dựng Đồ thị Hoàn tất ---")
    print(f"Đồ thị cuối cùng có {final_graph.number_of_nodes()} nút và {final_graph.number_of_edges()} cạnh.")


In [ ]:
if __name__ == "__main__":

    # Danh mục cổ phiếu và lĩnh vực (ví dụ)
    my_portfolio = ["FPT", "SSI", "VCB", "VHM", "HPG", "GAS", "MSN", "MWG", "GVR", "VCG"]
    my_portfolio_sector = ["Công nghệ", "Chứng khoán", "Ngân hàng", "Bất động sản", "Vật liệu cơ bản", "Dịch vụ Hạ tầng", "Tiêu dùng cơ bản", "Bán lẻ", "Chế biến", "Công nghiệp"]

    # --- Gọi hàm xây dựng đồ thị với lọc theo ngày ---
    # Chỉ định ngày bắt đầu và kết thúc để lọc bài báo
    # Định dạng YYYY-MM-DD
    start_filter_date = "2025-03-10"
    end_filter_date = "2025-03-11"

    print(f"\nBắt đầu xây dựng đồ thị cho các bài báo từ {start_filter_date} đến {end_filter_date}")
    final_graph = build_knowledge_graph(
        df=df_articles,
        portfolio=my_portfolio,
        portfolio_sector=my_portfolio_sector,
        skip=0,
        use_threading=False,  # Tắt xử lý song song
        max_frontier_size=5,
        max_workers=5,
        graph_checkpoint="knowledge_graph_p3_checkpoint_100.pkl",
        canonical_checkpoint="canonical_set_checkpoint_100.pkl",
        start_date=start_filter_date,
        end_date=end_filter_date
    )

    print("\n--- Xây dựng Đồ thị Hoàn tất ---")
    print(f"Đồ thị cuối cùng có {final_graph.number_of_nodes()} nút và {final_graph.number_of_edges()} cạnh.")


Bắt đầu xây dựng đồ thị cho các bài báo từ 2025-03-10 đến 2025-03-11
Đang tải đồ thị tri thức từ file cuối cùng: /content/knowledge_graph_p3_9-10.pkl
Đã tải đồ thị với 57 nút và 149 cạnh từ file cuối cùng.
Đang tải các thực thể chuẩn hóa từ file cuối cùng: /content/canonical_set_9-10.pkl
Đã tải 37 thực thể chuẩn hóa từ file cuối cùng.
Đã lọc bài báo từ ngày: 2025-03-10
Đã lọc bài báo đến ngày: 2025-03-11

Đang xử lý bài báo từ postID 865 đến 874
Chỉ số: 864, thực thể ban đầu (Tổng hợp): 1
Processing batch with 3 relationships using timestamp: 2025-03-10 09:00:00+00:00
Chỉ số: 864, frontier tiếp theo: 1
Processing batch with 1 relationships using timestamp: 2025-03-10 09:00:00+00:00
Chỉ số: 864, frontier tiếp theo: 1
Chỉ số: 865, thực thể ban đầu (Tổng hợp): 3
Processing batch with 12 relationships using timestamp: 2025-03-10 09:00:00+00:00
Chỉ số: 865, frontier tiếp theo: 4
Processing batch with 13 relationships using timestamp: 2025-03-10 09:00:00+00:00
Chỉ số: 865, frontier tiếp the

In [ ]:
import time 
if __name__ == "__main__":
    # Ghi lại thời điểm bắt đầu chạy cell
    start_time = time.time()

    # Danh mục cổ phiếu và lĩnh vực (ví dụ)
    my_portfolio = ["FPT", "SSI", "VCB", "VHM", "HPG", "GAS", "MSN", "MWG", "GVR", "VCG"]
    my_portfolio_sector = ["Công nghệ", "Chứng khoán", "Ngân hàng", "Bất động sản", "Vật liệu cơ bản", "Dịch vụ Hạ tầng", "Tiêu dùng cơ bản", "Bán lẻ", "Chế biến", "Công nghiệp"]

    # --- Gọi hàm xây dựng đồ thị với lọc theo ngày ---
    # Chỉ định ngày bắt đầu và kết thúc để lọc bài báo
    # Định dạng YYYY-MM-DD
    start_filter_date = "2025-04-07"
    end_filter_date = "2025-04-08"

    print(f"\nBắt đầu xây dựng đồ thị cho các bài báo từ {start_filter_date} đến {end_filter_date}")
    final_graph = build_knowledge_graph(
        df=df_articles,
        portfolio=my_portfolio,
        portfolio_sector=my_portfolio_sector,
        skip=0,
        use_threading=False,   # Tắt xử lý song song
        max_frontier_size=5,
        max_workers=5,
        graph_checkpoint="knowledge_graph_p3_checkpoint_100.pkl",
        canonical_checkpoint="canonical_set_checkpoint_100.pkl",
        start_date=start_filter_date,
        end_date=end_filter_date
    )

    print("\n--- Xây dựng Đồ thị Hoàn tất ---")
    print(f"Đồ thị cuối cùng có {final_graph.number_of_nodes()} nút và {final_graph.number_of_edges()} cạnh.")

    # Ghi lại thời điểm kết thúc chạy cell
    end_time = time.time()
    # Tính toán thời gian chạy
    elapsed_time = end_time - start_time

    # Chuyển đổi thời gian sang phút và giây để dễ đọc hơn
    minutes = int(elapsed_time // 60)
    seconds = elapsed_time % 60

    print(f"\n--- Thời gian chạy của cell này: {minutes} phút và {seconds:.2f} giây ---")

Asking to truncate to max_length but no maximum length is provided and the model has no predefined maximum length. Default to no truncation.



Bắt đầu xây dựng đồ thị cho các bài báo từ 2025-04-07 đến 2025-04-08
Đã lọc bài báo từ ngày: 2025-04-07
Đã lọc bài báo đến ngày: 2025-04-08

Đang xử lý bài báo từ postID 1425 đến 1434
Bài báo 1424: NER không trích xuất được thực thể. Đang chuyển sang LLM fallback.
Bài báo 1424: Đã sử dụng LLM fallback để trích xuất thực thể.
Chỉ số: 1424, thực thể ban đầu (Tổng hợp): 5
Processing batch with 12 relationships using timestamp: 2025-04-07 09:00:00+00:00
Chỉ số: 1424, frontier tiếp theo: 5
Processing batch with 26 relationships using timestamp: 2025-04-07 09:00:00+00:00
Chỉ số: 1424, frontier tiếp theo: 5
Bài báo 1425: NER không trích xuất được thực thể. Đang chuyển sang LLM fallback.
Bài báo 1425: Đã sử dụng LLM fallback để trích xuất thực thể.
Chỉ số: 1425, thực thể ban đầu (Tổng hợp): 5
Processing batch with 15 relationships using timestamp: 2025-04-07 09:00:00+00:00
Chỉ số: 1425, frontier tiếp theo: 5
Processing batch with 13 relationships using timestamp: 2025-04-07 09:00:00+00:00
Chỉ

  quota_metric: "generativelanguage.googleapis.com/generate_content_free_tier_requests"
  quota_id: "GenerateRequestsPerMinutePerProjectPerModel-FreeTier"
  quota_dimensions {
    key: "model"
    value: "gemini-2.0-flash"
  }
  quota_dimensions {
    key: "location"
    value: "global"
  }
  quota_value: 15
}
, links {
  description: "Learn more about Gemini API quotas"
  url: "https://ai.google.dev/gemini-api/docs/rate-limits"
}
, retry_delay {
  seconds: 39
}
].


Processing batch with 3 relationships using timestamp: 2025-04-07 09:00:00+00:00
Chỉ số: 1437, frontier tiếp theo: 3
Lỗi 429: Thử lại sau 37.33563970946258 giây... (Lần thử 1/3)


  quota_metric: "generativelanguage.googleapis.com/generate_content_free_tier_requests"
  quota_id: "GenerateRequestsPerDayPerProjectPerModel-FreeTier"
  quota_dimensions {
    key: "model"
    value: "gemini-2.0-flash"
  }
  quota_dimensions {
    key: "location"
    value: "global"
  }
  quota_value: 200
}
, links {
  description: "Learn more about Gemini API quotas"
  url: "https://ai.google.dev/gemini-api/docs/rate-limits"
}
, retry_delay {
}
].


...

Lỗi 429: Thử lại sau 58.72904180152606 giây... (Lần thử 2/3)


  quota_metric: "generativelanguage.googleapis.com/generate_content_free_tier_requests"
  quota_id: "GenerateRequestsPerDayPerProjectPerModel-FreeTier"
  quota_dimensions {
    key: "model"
    value: "gemini-2.0-flash"
  }
  quota_dimensions {
    key: "location"
    value: "global"
  }
  quota_value: 200
}
, links {
  description: "Learn more about Gemini API quotas"
  url: "https://ai.google.dev/gemini-api/docs/rate-limits"
}
, retry_delay {
  seconds: 59
}
].


Lỗi 429: Thử lại sau 57.730770551519974 giây... (Lần thử 3/3)


  quota_metric: "generativelanguage.googleapis.com/generate_content_free_tier_requests"
  quota_id: "GenerateRequestsPerDayPerProjectPerModel-FreeTier"
  quota_dimensions {
    key: "model"
    value: "gemini-2.0-flash"
  }
  quota_dimensions {
    key: "location"
    value: "global"
  }
  quota_value: 200
}
, links {
  description: "Learn more about Gemini API quotas"
  url: "https://ai.google.dev/gemini-api/docs/rate-limits"
}
, retry_delay {
  seconds: 59
}
].


Đã đạt số lần thử lại tối đa. Lỗi: 429 You exceeded your current quota, please check your plan and billing details. For more information on this error, head to: https://ai.google.dev/gemini-api/docs/rate-limits. [violations {
  quota_metric: "generativelanguage.googleapis.com/generate_content_free_tier_requests"
  quota_id: "GenerateRequestsPerDayPerProjectPerModel-FreeTier"
  quota_dimensions {
    key: "model"
    value: "gemini-2.0-flash"
  }
  quota_dimensions {
    key: "location"
    value: "global"
  }
  quota_value: 200
}
, links {
  description: "Learn more about Gemini API quotas"
  url: "https://ai.google.dev/gemini-api/docs/rate-limits"
}
, retry_delay {
  seconds: 57
}
]
Chỉ số: 1443, frontier tiếp theo: 0
Đã lưu checkpoint sau khi xử lý postID đến 1444
Đồ thị hiện có 75 nút và 235 cạnh

Hoàn thành xây dựng đồ thị. Đồ thị cuối cùng đã được lưu vào '/content/merged_knowledge_graph_0104.pkl' và '/content/merged_canonical_set_0104.pkl'.

Hoàn thành xây dựng đồ thị với 75 nút 

In [ ]:
#1202-1204
#1301-1304

In [ ]:
# --- Các hàm hỗ trợ ---
def graph_entities_to_str(G):
    """
    Lấy chuỗi các nút loại "entity" từ đồ thị để làm ngữ cảnh cho LLM.
    """
    entities = [node for node in G.nodes() if G.nodes[node].get("type") == "entity"]
    graph_str = ", ".join(entities)
    return graph_str[:20000] if len(graph_str) > 20000 else graph_str

import re

def invoke_chain_with_retry(chain, prompt, max_retries=MAX_RETRIES, base_delay=BASE_DELAY):
    retry_count = 0
    while True:
        try:
            response = chain.invoke(prompt)
            time.sleep(5)  # Độ trễ cố định
            return response
        except ResourceExhausted as e:
            retry_count += 1
            if retry_count > max_retries:
                print(f"Đã đạt số lần thử lại tối đa. Lỗi: {e}")
                return None
            retry_after = base_delay
            error_str = str(e)
            match = re.search(r'retry_delay\s*\{\s*seconds:\s*(\d+)\s*\}', error_str)
            if match:
                retry_after = float(match.group(1))
            delay = retry_after + random.uniform(0, 1)  # Thêm jitter
            print(f"Lỗi 429: Thử lại sau {delay} giây... (Lần thử {retry_count}/{max_retries})")
            time.sleep(delay)
        except Exception as e:
            retry_count += 1
            if retry_count > max_retries:
                print(f"Đã đạt số lần thử lại tối đa. Lỗi: {e}")
                return None
            delay = base_delay * (2 ** (retry_count - 1))
            print(f"Lỗi: {e}. Thử lại sau {delay} giây... (Lần thử {retry_count}/{max_retries})")
            time.sleep(delay)

def parse_entity_response(response):
    """
    Parses the response from the entity extraction prompt (LLM fallback).
    """
    if response is None:
        print("Phản hồi LLM là None.")
        return {"POSITIVE": [], "NEGATIVE": []}

    sections = {"POSITIVE": [], "NEGATIVE": []}
    current_section = None
    str_resp = response.content

    for line in str(str_resp).splitlines():
        line = line.strip()
        if not line:
            continue
        if "[[POSITIVE]]" in line.upper():
            current_section = "POSITIVE"
            continue
        if "[[NEGATIVE]]" in line.upper():
            current_section = "NEGATIVE"
            continue
        if current_section and ':' in line:
            entity = line.split(":", 1)[0].strip()
            if not entity or "không có thực thể nào" in entity.lower():
                continue
            content = line.split(entity, 1)[-1].strip(':').strip()
            sections[current_section].append((entity, content))
    return sections

def parse_batch_entity_response(response):
    """
    Phân tích phản hồi từ prompt trích xuất mối quan hệ theo lô.
    Trả về danh sách các tuple (source_entity, impact, target_entity, content).
    """
    if response is None:
        print("Phản hồi là None.")
        return []

    results = []
    current_source = None
    current_impact = None
    current_section = None

    str_resp = str(response.content)
    lines = str_resp.splitlines()

    for line in lines:
        line = line.strip()
        if not line:
            continue

        if line.startswith("[[SOURCE:") or "[[SOURCE:" in line:
            source_text = line.replace("[[SOURCE:", "").replace("]]", "").strip()
            if source_text and "không có thực thể nào" not in source_text.lower():
                current_source = source_text
            else:
                current_source = None
            current_impact = None # Reset impact for new source
            current_section = None # Reset section for new source
            continue

        if line.startswith("[[IMPACT:") or "[[IMPACT:" in line:
            impact_str = line.replace("[[IMPACT:", "").replace("]]", "").strip()
            current_impact = impact_str.upper()
            continue

        if "[[POSITIVE]]" in line.upper():
            current_section = "POSITIVE"
            continue

        if "[[NEGATIVE]]" in line.upper():
            current_section = "NEGATIVE"
            continue

        if current_source and current_section and ':' in line:
            try:
                entity, *content_parts = line.split(":", 1)
                entity = entity.strip().strip('[]')

                if not entity or "không có thực thể nào" in entity.lower():
                    continue

                if entity and content_parts:
                    content = content_parts[0].strip()
                    actual_impact = current_impact if current_impact else current_section
                    results.append((current_source, actual_impact, entity, content))
            except Exception as e:
                print(f"Lỗi phân tích dòng: {line}. Lỗi: {e}")
                continue

    if not results:
        print("Cảnh báo: Không có mối quan hệ nào được phân tích từ phản hồi.")
        print(f"Nội dung phản hồi: {str_resp[:500]}...")

    return results

def merge_entity(entity, canonical_set):
    """
    Trả về phiên bản chuẩn hóa của thực thể nếu đã có (không phân biệt chữ hoa/thường),
    nếu không thì thêm và trả về thực thể mới.
    """
    normalized_entity = str(entity).strip('[').strip(']').strip(' ').lower()
    for exist in canonical_set:
        if exist.lower() == normalized_entity:
            return exist
    canonical_set.add(normalized_entity)
    return normalized_entity

def add_edge(G, source, target, impact, timestamp):
    """
    Thêm một cạnh vào đồ thị nếu nó chưa tồn tại.
    """
    if not G.has_edge(source, target):
        G.add_edge(source, target, impact=impact, timestamp=timestamp)

# --- Hàm trích xuất thực thể thô bằng Deep Learning ---
def extract_entities_with_dl_model(text):
    """
    Sử dụng mô hình Deep Learning NER để trích xuất TÊN THỰC THỂ.
    Trả về danh sách các thực thể thô được trích xuất.
    """
    extracted_data = []
    try:
        ner_results = nlp_ner_pipeline(text)

        for ent_info in ner_results:
            entity_name = ent_info['word'].strip()
            if entity_name and len(entity_name) > 1 and ent_info.get('score', 0) > 0.7:
                extracted_data.append(entity_name)
        return extracted_data
    except Exception as e:
        print(f"Lỗi khi gọi mô hình Deep Learning NER: {e}")
        return []

# --- Hàm xác định tác động (Impact) bằng mô hình phân loại cảm xúc nhỏ ---
def determine_impact_by_sentiment_model(text_to_analyze):
    """
    Sử dụng mô hình phân loại cảm xúc để gán tác động (POSITIVE/NEGATIVE).
    """
    try:
        sentiment_result = nlp_sentiment_pipeline(text_to_analyze)

        if sentiment_result and len(sentiment_result) > 0:
            label = sentiment_result[0]['label']
            score = sentiment_result[0]['score']

            if label == "LABEL_1" and score > 0.7:
                return "POSITIVE"
            elif label == "LABEL_0" and score > 0.7:
                return "NEGATIVE"
        return "POSITIVE" # Mặc định là tích cực nếu không rõ ràng hoặc độ tin cậy thấp
    except Exception as e:
        print(f"Lỗi khi gọi mô hình phân loại cảm xúc: {e}")
        return "POSITIVE" # Fallback nếu có lỗi

def batch_process_entity_relationships(entity_batch, G, canonical_entities, portfolio, portfolio_str_full, article_timestamp):
    """
    Process multiple entities in a single API call
    Returns a list of new entities to process
    """
    if not entity_batch:
        return []

    max_batch_retries = 2
    batch_retry_count = 0
    relationships = []

    while batch_retry_count < max_batch_retries:
        input_entities_text = ""
        for entity, impact, content in entity_batch:
            input_entities_text += f"Thực thể gốc: {entity}\n\nẢnh hưởng: {impact}, {content}\n\n---\n\n"

        prompt_batch = {
            "input_entities": input_entities_text,
            "portfolio": portfolio_str_full,
            "existing_entities": graph_entities_to_str(G)
        }

        response = invoke_chain_with_retry(chain_batch_relation, prompt_batch)
        time.sleep(10)

        if response is None:
            return []

        relationships = parse_batch_entity_response(response)

        if len(relationships) > 0:
            break

        batch_retry_count += 1
        print(f"Batch processing returned 0 relationships. Retry {batch_retry_count}/{max_batch_retries}")
        time.sleep(BASE_DELAY)

    print(f"Processing batch with {len(relationships)} relationships using timestamp: {article_timestamp}")

    next_entities = []

    for source, impact, target, content in relationships:
        if "không có thực thể nào" in source.lower() or "không có thực thể nào" in target.lower():
            continue

        canon_source = source
        canon_target = merge_entity(target, canonical_entities)

        node_type = "stock" if any(str(canon_target).lower().find(stock.lower()) != -1 for stock in portfolio) else "entity"

        if not G.has_node(canon_target):
            G.add_node(canon_target, type=node_type, timestamp=article_timestamp)

        add_edge(G, canon_source, canon_target, impact, article_timestamp)

        if node_type == "entity":
            next_entities.append((canon_target, impact, content))

    return next_entities

# --- Hàm process_article (Giữ nguyên như yêu cầu của bạn) ---
def process_article(idx, row, G, canonical_entities, portfolio, portfolio_sector, max_frontier_size=5):
    """
    Xử lý một bài báo để trích xuất thực thể và xây dựng mối quan hệ.
    Sử dụng mô hình Deep Learning cho trích xuất thực thể ban đầu và phân loại cảm xúc cho tác động,
    với fallback về LLM nếu DL không thành công.
    """
    portfolio_str_full = ", ".join([f"{stock}-{sector}" for stock, sector in zip(portfolio, portfolio_sector)])

    article_node = f"Article_{row['postID']}" # Sử dụng postID thay cho idx cho rõ ràng
    article_timestamp = row['parsed_date']

    if G.has_node(article_node):
        print(f"Cảnh báo: Bài báo {row['postID']} đã tồn tại trong đồ thị. Bỏ qua xử lý lại.")
        return 0, 0

    new_nodes = 0
    new_edges = 0

    use_llm_fallback = False

    article_full_text = f"Tiêu đề: {row['title']}. Mô tả: {row['description']}"

    raw_dl_entities = extract_entities_with_dl_model(article_full_text)

    if not raw_dl_entities:
        print(f"Bài báo {row['postID']}: NER không trích xuất được thực thể. Đang chuyển sang LLM fallback.")
        use_llm_fallback = True

    entities_with_impact = {"POSITIVE": [], "NEGATIVE": []}

    if not use_llm_fallback:
        for ent_name in raw_dl_entities:
            impact = determine_impact_by_sentiment_model(row['description'])
            ent_content_summary = row['description']

            if impact == "POSITIVE":
                entities_with_impact["POSITIVE"].append((ent_name, ent_content_summary))
            elif impact == "NEGATIVE":
                entities_with_impact["NEGATIVE"].append((ent_name, ent_content_summary))

        if not (entities_with_impact["POSITIVE"] or entities_with_impact["NEGATIVE"]):
            print(f"Bài báo {row['postID']}: SA không gán được tác động hợp lệ cho thực thể DL. Đang chuyển sang LLM fallback.")
            use_llm_fallback = True

    if use_llm_fallback:
        prompt_text = {
            "portfolio": portfolio_str_full,
            "date": row['date'],
            "group": row['group'],
            "title": row['title'],
            "description": row['description'],
            "existing_entities": graph_entities_to_str(G)
        }

        response_text = invoke_chain_with_retry(chain_entity, prompt_text)

        if response_text is None:
            print(f"Bỏ qua bài báo {row['postID']} do lỗi API LLM (fallback).")
            return 0, 0

        entities_dict_from_llm = parse_entity_response(response_text)
        entities_with_impact = entities_dict_from_llm
        print(f"Bài báo {row['postID']}: Đã sử dụng LLM fallback để trích xuất thực thể.")

    total_entities = len(entities_with_impact.get("POSITIVE", [])) + len(entities_with_impact.get("NEGATIVE", []))
    if total_entities == 0:
        print(f"Không thể trích xuất hoặc gán tác động cho thực thể từ bài báo {row['postID']} sau cả DL và LLM fallback.")
        return 0, 0

    initial_entities = []
    for impact_type in ["POSITIVE", "NEGATIVE"]:
        for ent, content in entities_with_impact.get(impact_type, []):
            if not ent or "không có thực thể nào" in ent.lower():
                continue

            canon_ent = merge_entity(ent, canonical_entities)
            node_type = "stock" if any(str(canon_ent).lower().find(stock.lower()) != -1 for stock in portfolio) else "entity"

            if not G.has_node(canon_ent):
                G.add_node(canon_ent, type=node_type, timestamp=article_timestamp)
                new_nodes += 1

            if node_type == "entity":
                initial_entities.append((canon_ent, impact_type, content))

            add_edge(G, article_node, canon_ent, impact_type, article_timestamp)
            new_edges += 1

    print(f"Bài báo {row['postID']}, thực thể ban đầu (Tổng hợp): {len(initial_entities)}")

    frontier = initial_entities
    iter_count = 0
    MAX_ITER = 2

    while frontier and iter_count < MAX_ITER:
        if len(frontier) > max_frontier_size:
            frontier = random.sample(frontier, max_frontier_size)
            print(f"Bài báo {row['postID']}, giới hạn frontier xuống {max_frontier_size} thực thể")

        next_frontier = batch_process_entity_relationships(
            frontier, G, canonical_entities, portfolio, portfolio_str_full, article_timestamp
        )

        frontier = list({ent: (ent, imp, txt) for ent, imp, txt in next_frontier}.values())
        if len(frontier) > max_frontier_size:
            frontier = random.sample(frontier, max_frontier_size)

        print(f"Bài báo {row['postID']}, frontier tiếp theo: {len(frontier)}")
        iter_count += 1

    return new_nodes, new_edges

# --- Hàm build_knowledge_graph hiện có của bạn (Đã có sẵn, không thay đổi) ---
def build_knowledge_graph(df, portfolio, portfolio_sector, skip=0, use_threading=True, max_frontier_size=5, max_workers=2,
                          graph_checkpoint=None, canonical_checkpoint=None, start_date=None, end_date=None, articles_per_batch=5, delay_between_batches_seconds=60):
    """
    Xây dựng đồ thị tri thức từ các bài báo với xử lý theo lô được tối ưu hóa.
    Xử lý nhiều bài báo song song bằng cách sử dụng luồng.
    Cho phép lọc bài báo theo ngày.
    Nếu file knowledge_graph_p3.pkl tồn tại, sẽ load và thêm vào đồ thị hiện có.
    Nếu không, sẽ tạo mới và lưu.
    Thêm tùy chọn để tạm dừng sau mỗi N bài báo.
    """
    G = nx.DiGraph()
    canonical_entities = set()

    final_graph_output_file = "/content/merged_knowledge_graph_0704.pkl"
    final_canonical_output_file = "/content/merged_canonical_set_0704.pkl"

    # --- Sửa đổi chính ở đây: Kiểm tra và tải đồ thị/thực thể cuối cùng trước tiên ---
    if os.path.exists(final_graph_output_file):
        print(f"Đang tải đồ thị tri thức từ file cuối cùng: {final_graph_output_file}")
        try:
            with open(final_graph_output_file, "rb") as f:
                G = pickle.load(f)
            print(f"Đã tải đồ thị với {G.number_of_nodes()} nút và {G.number_of_edges()} cạnh từ file cuối cùng.")
        except Exception as e:
            print(f"Lỗi khi tải đồ thị từ file cuối cùng '{final_graph_output_file}': {e}")
            print("Bắt đầu với đồ thị rỗng.")
            G = nx.DiGraph() # Đảm bảo G là đồ thị rỗng nếu lỗi

    if os.path.exists(final_canonical_output_file):
        print(f"Đang tải các thực thể chuẩn hóa từ file cuối cùng: {final_canonical_output_file}")
        try:
            with open(final_canonical_output_file, "rb") as f:
                canonical_entities = pickle.load(f)
            print(f"Đã tải {len(canonical_entities)} thực thể chuẩn hóa từ file cuối cùng.")
        except Exception as e:
            print(f"Lỗi khi tải thực thể chuẩn hóa từ file cuối cùng '{final_canonical_output_file}': {e}")
            print("Bắt đầu với tập hợp thực thể chuẩn hóa rỗng.")
            canonical_entities = set() # Đảm bảo canonical_entities là tập hợp rỗng nếu lỗi
    # --- Kết thúc sửa đổi chính ---
    if graph_checkpoint and os.path.exists(graph_checkpoint) and not os.path.exists(final_graph_output_file):
        print(f"Đang tải đồ thị tri thức từ checkpoint: {graph_checkpoint}")
        try:
            temp_G = pickle.load(f)
            G.add_nodes_from(temp_G.nodes(data=True))
            G.add_edges_from(temp_G.edges(data=True))
            print(f"Đã thêm đồ thị từ checkpoint với {temp_G.number_of_nodes()} nút và {temp_G.number_of_edges()} cạnh vào đồ thị hiện có.")
        except Exception as e:
            print(f"Lỗi khi tải checkpoint đồ thị: {e}")
            print("Bắt đầu với đồ thị rỗng.")

    if canonical_checkpoint and os.path.exists(canonical_checkpoint) and not os.path.exists(final_canonical_output_file):
        print(f"Đang tải các thực thể chuẩn hóa từ checkpoint: {canonical_checkpoint}")
        try:
            temp_canonical_entities = set()
            with open(canonical_checkpoint, "rb") as f:
                temp_canonical_entities = pickle.load(f)
            canonical_entities.update(temp_canonical_entities) # Hợp nhất các thực thể
            print(f"Đã thêm {len(temp_canonical_entities)} thực thể chuẩn hóa từ checkpoint vào tập hợp hiện có.")
        except Exception as e:
            print(f"Lỗi khi tải checkpoint thực thể chuẩn hóa: {e}")
            print("Bắt đầu với tập hợp thực thể chuẩn hóa rỗng.")


    df['parsed_date'] = pd.to_datetime(df['date'], utc=True)

    if start_date:
        start_filter_dt = pd.to_datetime(start_date, utc=True)
        df = df[df['parsed_date'] >= start_filter_dt]
        print(f"Đã lọc bài báo từ ngày: {start_date}")
    if end_date:
        end_filter_dt = pd.to_datetime(end_date, utc=True)
        df = df[df['parsed_date'] <= end_filter_dt]
        print(f"Đã lọc bài báo đến ngày: {end_date}")

    if skip > 0:
        print(f"Bỏ qua {skip} bài báo đầu tiên")
        df = df.iloc[skip:]

    if df.empty:
        print("DataFrame rỗng sau khi lọc. Không có bài báo nào để xử lý.")
        # Lưu đồ thị hiện có (nếu có) trước khi thoát
        try:
            with open(final_graph_output_file, "wb") as f:
                pickle.dump(G, f)
            with open(final_canonical_output_file, "wb") as f:
                pickle.dump(canonical_entities, f)
            print(f"Đồ thị cuối cùng và tập hợp thực thể đã được lưu (không có bài báo mới được xử lý).")
        except Exception as e:
            print(f"Cảnh báo: Lỗi khi lưu đồ thị/thực thể khi DataFrame rỗng: {e}")
        return G

    # Thay đổi chunk_size thành articles_per_batch
    for chunk_start in range(0, len(df), articles_per_batch):
        chunk_end = min(chunk_start + articles_per_batch, len(df))
        chunk_df = df.iloc[chunk_start:chunk_end]

        postid_start = chunk_df['postID'].iloc[0]
        postid_end = chunk_df['postID'].iloc[-1]
        print(f"\nĐang xử lý bài báo từ postID {postid_start} đến {postid_end}")

        if use_threading and len(chunk_df) > 1:
            articles_processed_in_chunk = 0
            with ThreadPoolExecutor(max_workers=min(max_workers, len(chunk_df))) as executor:
                futures = [
                    executor.submit(
                        process_article,
                        idx,
                        row,
                        G, # Truyền G trực tiếp để các luồng có thể sửa đổi nó
                        canonical_entities, # Truyền canonical_entities trực tiếp
                        portfolio,
                        portfolio_sector,
                        max_frontier_size
                    )
                    for idx, row in chunk_df.iterrows()
                ]

                for future in futures:
                    future.result() # Đảm bảo chờ kết quả để bắt exception nếu có
                    articles_processed_in_chunk += 1

            print(f"Đã xử lý {articles_processed_in_chunk} bài báo song song trong chunk này.")
        else:
            for idx, row in chunk_df.iterrows():
                process_article(
                    idx,
                    row,
                    G,
                    canonical_entities,
                    portfolio,
                    portfolio_sector,
                    max_frontier_size
                )

        # Thêm thời gian chờ sau mỗi chunk
        if chunk_end < len(df): # Chỉ chờ nếu còn bài báo để xử lý
            print(f"Đã xử lý {articles_per_batch} bài báo. Tạm dừng {delay_between_batches_seconds} giây để tránh lỗi API 429...")
            time.sleep(delay_between_batches_seconds)


    # --- Lưu đồ thị và tập hợp chuẩn hóa cuối cùng ---
    try:
        output_graph_dir = os.path.dirname(final_graph_output_file)
        if output_graph_dir:
            os.makedirs(output_graph_dir, exist_ok=True)
        with open(final_graph_output_file, "wb") as f:
            pickle.dump(G, f)
        print(f"\nĐồ thị cuối cùng đã được lưu vào '{final_graph_output_file}'.")
    except Exception as e:
        print(f"Lỗi khi lưu đồ thị cuối cùng vào file '{final_graph_output_file}': {e}")

    try:
        output_canonical_set_dir = os.path.dirname(final_canonical_output_file)
        if output_canonical_set_dir:
            os.makedirs(output_canonical_set_dir, exist_ok=True)
        with open(final_canonical_output_file, "wb") as f:
            pickle.dump(canonical_entities, f)
        print(f"Tập hợp thực thể chuẩn hóa cuối cùng đã được lưu vào '{final_canonical_output_file}'.")
    except Exception as e:
        print(f"Lỗi khi lưu tập hợp thực thể chuẩn hóa cuối cùng vào file '{final_canonical_output_file}': {e}")

    return G


# if __name__ == "__main__":
#     # --- 1. Tải DataFrame của bạn ---
#     try:
#         df_articles = pd.read_csv('/content/summerized_articles(1).csv')
#         df_articles['date'] = pd.to_datetime(df_articles['date'])
#         # Đảm bảo cột 'postID' là int nếu có thể
#         if 'postID' in df_articles.columns:
#             df_articles['postID'] = df_articles['postID'].astype(int)
#         print("Đã tải file CSV thành công.")
#     except FileNotFoundError:
#         print("Lỗi: Không tìm thấy file '/content/summarized_articles(1).csv'. Vui lòng kiểm tra đường dẫn.")
#     except Exception as e:
#         print(f"Lỗi khi đọc file CSV: {e}. Đang sử dụng DataFrame giả lập.")

#     my_portfolio= ["FPT", "SSI", "VCB", "VHM", "HPG", "GAS", "MSN", "MWG", "GVR", "VCG"]
#     my_portfolio_sector = ["Công nghệ", "Chứng khoán", "Ngân hàng", "Bất động sản", "Vật liệu cơ bản", "Dịch vụ Hạ tầng", "Tiêu dùng cơ bản", "Bán lẻ", "Chế biến", "Công nghiệp"]

#     # --- 3. Tải đồ thị và canonical_set hiện có để tìm các postID đã xử lý ---
#     # Đường dẫn đến các file đồ thị và canonical_set đã lưu
#     graph_file_path = "/content/merged_knowledge_graph_0704.pkl"
#     canonical_set_file_path = "/content/merged_canonical_set_0704.pkl"

#     existing_G = nx.DiGraph()

#     if os.path.exists(graph_file_path):
#         try:
#             with open(graph_file_path, "rb") as f:
#                 existing_G = pickle.load(f)
#             print(f"Đã tải đồ thị hiện có với {existing_G.number_of_nodes()} nút và {existing_G.number_of_edges()} cạnh.")
#         except Exception as e:
#             print(f"Lỗi khi tải đồ thị hiện có: {e}. Bắt đầu với đồ thị rỗng.")
#             existing_G = nx.DiGraph()
#     else:
#         print(f"File đồ thị '{graph_file_path}' không tồn tại. Đang tạo đồ thị rỗng để bắt đầu.")
#         # Tạo file rỗng nếu chưa có, để build_knowledge_graph có thể ghi vào
#         with open(graph_file_path, "wb") as f:
#             pickle.dump(existing_G, f)
#         with open(canonical_set_file_path, "wb") as f:
#             pickle.dump(set(), f)

#     # 4. Tìm tất cả các postID đã có trong đồ thị
#     # Các nút bài báo được đặt tên là "Article_postID"
#     processed_post_ids_in_graph = set()
#     for node in existing_G.nodes():
#         if isinstance(node, str) and node.startswith("Article_"):
#             try:
#                 post_id = int(node.split('_')[1])
#                 processed_post_ids_in_graph.add(post_id)
#             except ValueError:
#                 # Bỏ qua các nút Article không hợp lệ nếu có
#                 pass

#     print(f"Tìm thấy {len(processed_post_ids_in_graph)} bài báo đã được xử lý trong đồ thị.")

#     # 5. Lọc DataFrame để chỉ xử lý các bài báo CÓ postID KHÔNG CÓ trong đồ thị
#     df_articles_to_process = df_articles[~df_articles['postID'].isin(processed_post_ids_in_graph)].copy()

#     if df_articles_to_process.empty:
#         print("Không có bài báo nào trong file CSV chưa được xử lý trong đồ thị. Đồ thị đã hoàn thành hoặc bạn cần kiểm tra dữ liệu.")
#     else:
#         print(f"Đang xử lý {len(df_articles_to_process)} bài báo mới/thiếu...")
#         # Sử dụng hàm build_knowledge_graph đã có của bạn để tiếp tục
#         # Hàm này sẽ tự động tải đồ thị hiện có và thêm vào.
#         final_graph = build_knowledge_graph(
#             df=df_articles_to_process,
#             portfolio=my_portfolio,
#             portfolio_sector=my_portfolio_sector,
#             use_threading=True, # Bật threading để tăng tốc
#             max_workers=4, # Điều chỉnh số lượng worker tùy theo tài nguyên của bạn
#             articles_per_batch=5, # Xử lý 5 bài báo mỗi lần
#             delay_between_batches_seconds=60 # Dừng 60 giây sau mỗi 5 bài báo
#         )
#         print(f"\nQuá trình xây dựng đồ thị hoàn tất. Tổng số nút: {final_graph.number_of_nodes()}, Tổng số cạnh: {final_graph.number_of_edges()}.")

NameError: name 'MAX_RETRIES' is not defined

In [ ]:
try:
    df_articles = pd.read_csv('/content/summerized_articles(1).csv')
    df_articles['date'] = pd.to_datetime(df_articles['date'])
    # Đảm bảo cột 'postID' là int nếu có thể
    if 'postID' in df_articles.columns:
        df_articles['postID'] = df_articles['postID'].astype(int)
    print("Đã tải file CSV thành công.")
except FileNotFoundError:
    print("Lỗi: Không tìm thấy file '/content/summarized_articles(1).csv'. Vui lòng kiểm tra đường dẫn.")
except Exception as e:
    print(f"Lỗi khi đọc file CSV: {e}. Đang sử dụng DataFrame giả lập.")

my_portfolio= ["FPT", "SSI", "VCB", "VHM", "HPG", "GAS", "MSN", "MWG", "GVR", "VCG"]
my_portfolio_sector = ["Công nghệ", "Chứng khoán", "Ngân hàng", "Bất động sản", "Vật liệu cơ bản", "Dịch vụ Hạ tầng", "Tiêu dùng cơ bản", "Bán lẻ", "Chế biến", "Công nghiệp"]


Đã tải file CSV thành công.


In [ ]:
if __name__ == "__main__":
    # ... (các phần tải DataFrame, định nghĩa portfolio như cũ) ...

    # --- 3. Tải đồ thị và canonical_set hiện có (KHÔNG cần thay đổi) ---
    graph_file_path = "/content/merged_knowledge_graph_0704.pkl"
    canonical_set_file_path = "/content/merged_canonical_set_0704.pkl"

    existing_G = nx.DiGraph()
    if os.path.exists(graph_file_path):
        try:
            with open(graph_file_path, "rb") as f:
                existing_G = pickle.load(f)
            print(f"Đã tải đồ thị hiện có với {existing_G.number_of_nodes()} nút và {existing_G.number_of_edges()} cạnh.")
        except Exception as e:
            print(f"Lỗi khi tải đồ thị hiện có: {e}. Bắt đầu với đồ thị rỗng.")
            existing_G = nx.DiGraph()
    else:
        print(f"File đồ thị '{graph_file_path}' không tồn tại. Đang tạo đồ thị rỗng để bắt đầu.")
        with open(graph_file_path, "wb") as f:
            pickle.dump(existing_G, f)
        with open(canonical_set_file_path, "wb") as f:
            pickle.dump(set(), f)

    # KHI SỬ DỤNG PHƯƠNG PHÁP NÀY, BẠN CÓ THỂ BỎ QUA VIỆC TÌM processed_post_ids_in_graph
    # và chỉ định trực tiếp dải postID bạn muốn xử lý.

    # --- 4. Định nghĩa dải postID bạn muốn xử lý ---
    start_post_id = 983
    end_post_id = 1000
    # start_post_id = 1202
    # end_post_id = 1204
    # start_post_id = 1301
    # end_post_id = 1304

    df_articles_to_process = df_articles[
        (df_articles['postID'] >= start_post_id) & (df_articles['postID'] <= end_post_id)
    ].copy()

    if df_articles_to_process.empty:
        print(f"Không có bài báo nào trong dải postID {start_post_id}-{end_post_id} để xử lý.")
    else:
        print(f"Đang xử lý {len(df_articles_to_process)} bài báo trong dải postID từ {start_post_id} đến {end_post_id}...")
        # Sắp xếp lại DataFrame để đảm bảo xử lý theo thứ tự postID tăng dần
        df_articles_to_process = df_articles_to_process.sort_values(by='postID').reset_index(drop=True)

        final_graph = build_knowledge_graph(
            df=df_articles_to_process,
            portfolio=my_portfolio,
            portfolio_sector=my_portfolio_sector,
            use_threading=True,
            max_workers=4,
            articles_per_batch=5,
            delay_between_batches_seconds=60
        )
        print(f"\nQuá trình xây dựng đồ thị hoàn tất. Tổng số nút: {final_graph.number_of_nodes()}, Tổng số cạnh: {final_graph.number_of_edges()}.")

Đã tải đồ thị hiện có với 1763 nút và 10546 cạnh.
Đang xử lý 18 bài báo trong dải postID từ 983 đến 1000...
Đang tải đồ thị tri thức từ file cuối cùng: /content/merged_knowledge_graph_0704.pkl
Đã tải đồ thị với 1763 nút và 10546 cạnh từ file cuối cùng.
Đang tải các thực thể chuẩn hóa từ file cuối cùng: /content/merged_canonical_set_0704.pkl
Đã tải 1045 thực thể chuẩn hóa từ file cuối cùng.

Đang xử lý bài báo từ postID 983 đến 987
Bài báo 984: NER không trích xuất được thực thể. Đang chuyển sang LLM fallback.
Bài báo 986, thực thể ban đầu (Tổng hợp): 2
Bài báo 985, thực thể ban đầu (Tổng hợp): 3
Bài báo 983, thực thể ban đầu (Tổng hợp): 11
Bài báo 983, giới hạn frontier xuống 5 thực thể
Bài báo 984: Đã sử dụng LLM fallback để trích xuất thực thể.
Bài báo 984, thực thể ban đầu (Tổng hợp): 4
Processing batch with 5 relationships using timestamp: 2025-03-16 09:00:00+00:00
Bài báo 986, frontier tiếp theo: 5
Processing batch with 9 relationships using timestamp: 2025-03-16 09:00:00+00:00
Bà

In [ ]:
import networkx as nx
import pickle
import os

def merge_graphs_from_pkl(file_path1: str, file_path2: str, output_file_path: str = None) -> nx.DiGraph:
    """
    Hợp nhất hai đồ thị NetworkX từ các file PKL.

    Parameters:
    - file_path1 (str): Đường dẫn đến file PKL thứ nhất.
    - file_path2 (str): Đường dẫn đến file PKL thứ hai.
    - output_file_path (str, optional): Đường dẫn để lưu đồ thị đã hợp nhất vào file PKL mới.
                                        Nếu None, đồ thị sẽ không được lưu.

    Returns:
    - nx.DiGraph: Đồ thị đã hợp nhất.
    """
    graph1 = nx.DiGraph()
    graph2 = nx.DiGraph()

    # Bước 1: Tải đồ thị từ file PKL thứ nhất
    if os.path.exists(file_path1):
        try:
            with open(file_path1, 'rb') as f:
                graph1 = pickle.load(f)
            print(f"Đã tải đồ thị từ '{file_path1}' với {graph1.number_of_nodes()} nút và {graph1.number_of_edges()} cạnh.")
        except Exception as e:
            print(f"Lỗi khi tải đồ thị từ '{file_path1}': {e}")
            print(f"Sử dụng đồ thị rỗng cho '{file_path1}'.")
    else:
        print(f"File '{file_path1}' không tồn tại. Sử dụng đồ thị rỗng cho nó.")

    # Bước 2: Tải đồ thị từ file PKL thứ hai
    if os.path.exists(file_path2):
        try:
            with open(file_path2, 'rb') as f:
                graph2 = pickle.load(f)
            print(f"Đã tải đồ thị từ '{file_path2}' với {graph2.number_of_nodes()} nút và {graph2.number_of_edges()} cạnh.")
        except Exception as e:
            print(f"Lỗi khi tải đồ thị từ '{file_path2}': {e}")
            print(f"Sử dụng đồ thị rỗng cho '{file_path2}'.")
    else:
        print(f"File '{file_path2}' không tồn tại. Sử dụng đồ thị rỗng cho nó.")

    # Bước 3: Hợp nhất hai đồ thị
    # Đồ thị G1 sẽ được sửa đổi tại chỗ để thêm các nút và cạnh từ G2
    # Nếu có các nút trùng lặp, chúng sẽ được hợp nhất.
    # Nếu có các cạnh trùng lặp giữa cùng một cặp nút (u, v), NetworkX sẽ giữ lại cạnh đầu tiên được thêm
    # hoặc ghi đè thuộc tính tùy thuộc vào cách bạn xử lý. Với add_nodes_from và add_edges_from,
    # thuộc tính của các cạnh trùng lặp có thể được ghi đè nếu bạn thêm lại cùng một cặp (u,v).
    # Đối với các cạnh có thuộc tính `timestamp` (như trong ngữ cảnh của bạn), NetworkX sẽ tự động giữ lại
    # thuộc tính của cạnh khi nó được thêm vào lần đầu tiên hoặc nếu bạn không chỉ định cách xử lý xung đột.
    # Trong trường hợp này, các cạnh từ graph2 sẽ được thêm vào graph1. Nếu graph1 đã có cạnh (u,v),
    # thuộc tính của cạnh đó sẽ không bị thay đổi bởi việc thêm lại (u,v) từ graph2 trừ khi bạn gán lại.
    # Tuy nhiên, nếu bạn muốn xử lý xung đột thuộc tính cạnh (ví dụ: lấy thuộc tính mới nhất), bạn sẽ cần logic tùy chỉnh.
    # Với mục đích hợp nhất cơ bản, add_nodes_from và add_edges_from là đủ.

    merged_graph = nx.DiGraph() # Tạo một đồ thị mới để chứa kết quả hợp nhất
    merged_graph.add_nodes_from(graph1.nodes(data=True)) # Thêm tất cả nút và thuộc tính từ graph1
    merged_graph.add_edges_from(graph1.edges(data=True)) # Thêm tất cả cạnh và thuộc tính từ graph1

    merged_graph.add_nodes_from(graph2.nodes(data=True)) # Thêm/hợp nhất nút từ graph2
    merged_graph.add_edges_from(graph2.edges(data=True)) # Thêm/hợp nhất cạnh từ graph2

    print(f"\nĐồ thị đã hợp nhất có {merged_graph.number_of_nodes()} nút và {merged_graph.number_of_edges()} cạnh.")

    # Bước 4: Lưu đồ thị đã hợp nhất (nếu output_file_path được cung cấp)
    if output_file_path:
        output_dir = os.path.dirname(output_file_path)
        if output_dir: # Đảm bảo thư mục tồn tại nếu đường dẫn có thư mục con
            os.makedirs(output_dir, exist_ok=True)
        try:
            with open(output_file_path, 'wb') as f:
                pickle.dump(merged_graph, f)
            print(f"Đồ thị đã hợp nhất được lưu thành công tại '{output_file_path}'.")
        except Exception as e:
            print(f"Lỗi khi lưu đồ thị đã hợp nhất vào file '{output_file_path}': {e}")

    return merged_graph

# --- Ví dụ sử dụng ---
if __name__ == "__main__":

    # Thực hiện hợp nhất
    merged_result_graph = merge_graphs_from_pkl(
        "/content/knowledge_graph_p3_0803.pkl",
        "/content/knowledge_graph_p3_9-10.pkl",
        output_file_path="merged_knowledge_graph.pkl" # Tên file để lưu kết quả hợp nhất
    )

    print("\nKiểm tra đồ thị đã hợp nhất:")
    print(f"Nút trong đồ thị hợp nhất: {list(merged_result_graph.nodes(data=True))}")
    print(f"Cạnh trong đồ thị hợp nhất: {list(merged_result_graph.edges(data=True))}")

    # Xóa các file giả định sau khi thử nghiệm (tùy chọn)
    # os.remove("graph_alpha.pkl")
    # os.remove("graph_beta.pkl")
    # os.remove("merged_knowledge_graph.pkl")

Đã tải đồ thị G1 từ: /content/knowledge_graph_p3_9-10.pkl
Đã tải đồ thị G2 từ: /content/knowledge_graph_p3_0803.pkl

--- So sánh kích thước đồ thị ---
Đồ thị G1 có:
  - Số nút: 132
  - Số cạnh: 391

Đồ thị G2 có:
  - Số nút: 279
  - Số cạnh: 1389

--- Kết quả so sánh ---
Hai đồ thị G1 và G2 có kích thước khác nhau.
  G2 có nhiều nút hơn G1 (279 vs 132).
  G2 có nhiều cạnh hơn G1 (1389 vs 391).


In [ ]:
import networkx as nx
import pickle
import os

def merge_knowledge_bases_from_pkl(
    graph_file_path1: str,
    canonical_set_file_path1: str,
    graph_file_path2: str,
    canonical_set_file_path2: str,
    output_graph_file_path: str = None,
    output_canonical_set_file_path: str = None
) -> tuple[nx.DiGraph, set]:
    """
    Hợp nhất hai đồ thị NetworkX và hai tập hợp thực thể chuẩn hóa từ các file PKL.

    Parameters:
    - graph_file_path1 (str): Đường dẫn đến file PKL đồ thị thứ nhất.
    - canonical_set_file_path1 (str): Đường dẫn đến file PKL tập hợp chuẩn hóa thứ nhất.
    - graph_file_path2 (str): Đường dẫn đến file PKL đồ thị thứ hai.
    - canonical_set_file_path2 (str): Đường dẫn đến file PKL tập hợp chuẩn hóa thứ hai.
    - output_graph_file_path (str, optional): Đường dẫn để lưu đồ thị đã hợp nhất vào file PKL mới.
                                              Nếu None, đồ thị sẽ không được lưu.
    - output_canonical_set_file_path (str, optional): Đường dẫn để lưu tập hợp chuẩn hóa đã hợp nhất vào file PKL mới.
                                                        Nếu None, tập hợp chuẩn hóa sẽ không được lưu.

    Returns:
    - tuple[nx.DiGraph, set]: Một tuple chứa đồ thị đã hợp nhất và tập hợp chuẩn hóa đã hợp nhất.
    """
    graph1 = nx.DiGraph()
    graph2 = nx.DiGraph()
    canonical_set1 = set()
    canonical_set2 = set()

    # --- Tải Đồ thị 1 ---
    if os.path.exists(graph_file_path1):
        try:
            with open(graph_file_path1, 'rb') as f:
                graph1 = pickle.load(f)
            print(f"Đã tải đồ thị từ '{graph_file_path1}' với {graph1.number_of_nodes()} nút và {graph1.number_of_edges()} cạnh.")
        except Exception as e:
            print(f"Lỗi khi tải đồ thị từ '{graph_file_path1}': {e}")
            print(f"Sử dụng đồ thị rỗng cho '{graph_file_path1}'.")
    else:
        print(f"File '{graph_file_path1}' không tồn tại. Sử dụng đồ thị rỗng cho nó.")

    # --- Tải Canonical Set 1 ---
    if os.path.exists(canonical_set_file_path1):
        try:
            with open(canonical_set_file_path1, 'rb') as f:
                canonical_set1 = pickle.load(f)
            print(f"Đã tải tập hợp chuẩn hóa từ '{canonical_set_file_path1}' với {len(canonical_set1)} thực thể.")
        except Exception as e:
            print(f"Lỗi khi tải tập hợp chuẩn hóa từ '{canonical_set_file_path1}': {e}")
            print(f"Sử dụng tập hợp chuẩn hóa rỗng cho '{canonical_set_file_path1}'.")
    else:
        print(f"File '{canonical_set_file_path1}' không tồn tại. Sử dụng tập hợp chuẩn hóa rỗng cho nó.")

    # --- Tải Đồ thị 2 ---
    if os.path.exists(graph_file_path2):
        try:
            with open(graph_file_path2, 'rb') as f:
                graph2 = pickle.load(f)
            print(f"Đã tải đồ thị từ '{graph_file_path2}' với {graph2.number_of_nodes()} nút và {graph2.number_of_edges()} cạnh.")
        except Exception as e:
            print(f"Lỗi khi tải đồ thị từ '{graph_file_path2}': {e}")
            print(f"Sử dụng đồ thị rỗng cho '{graph_file_path2}'.")
    else:
        print(f"File '{graph_file_path2}' không tồn tại. Sử dụng đồ thị rỗng cho nó.")

    # --- Tải Canonical Set 2 ---
    if os.path.exists(canonical_set_file_path2):
        try:
            with open(canonical_set_file_path2, 'rb') as f:
                canonical_set2 = pickle.load(f)
            print(f"Đã tải tập hợp chuẩn hóa từ '{canonical_set_file_path2}' với {len(canonical_set2)} thực thể.")
        except Exception as e:
            print(f"Lỗi khi tải tập hợp chuẩn hóa từ '{canonical_set_file_path2}': {e}")
            print(f"Sử dụng tập hợp chuẩn hóa rỗng cho '{canonical_set_file_path2}'.")
    else:
        print(f"File '{canonical_set_file_path2}' không tồn tại. Sử dụng tập hợp chuẩn hóa rỗng cho nó.")

    # --- Hợp nhất hai đồ thị ---
    merged_graph = nx.DiGraph()
    merged_graph.add_nodes_from(graph1.nodes(data=True))
    merged_graph.add_edges_from(graph1.edges(data=True))
    merged_graph.add_nodes_from(graph2.nodes(data=True))
    merged_graph.add_edges_from(graph2.edges(data=True))

    print(f"\nĐồ thị đã hợp nhất có {merged_graph.number_of_nodes()} nút và {merged_graph.number_of_edges()} cạnh.")

    # --- Hợp nhất hai tập hợp chuẩn hóa ---
    merged_canonical_set = canonical_set1.union(canonical_set2)
    print(f"Tập hợp chuẩn hóa đã hợp nhất có {len(merged_canonical_set)} thực thể.")

    # --- Lưu đồ thị đã hợp nhất (nếu output_graph_file_path được cung cấp) ---
    if output_graph_file_path:
        output_graph_dir = os.path.dirname(output_graph_file_path)
        if output_graph_dir:
            os.makedirs(output_graph_dir, exist_ok=True)
        try:
            with open(output_graph_file_path, 'wb') as f:
                pickle.dump(merged_graph, f)
            print(f"Đồ thị đã hợp nhất được lưu thành công tại '{output_graph_file_path}'.")
        except Exception as e:
            print(f"Lỗi khi lưu đồ thị đã hợp nhất vào file '{output_graph_file_path}': {e}")

    # --- Lưu tập hợp chuẩn hóa đã hợp nhất (nếu output_canonical_set_file_path được cung cấp) ---
    if output_canonical_set_file_path:
        output_canonical_set_dir = os.path.dirname(output_canonical_set_file_path)
        if output_canonical_set_dir:
            os.makedirs(output_canonical_set_dir, exist_ok=True)
        try:
            with open(output_canonical_set_file_path, 'wb') as f:
                pickle.dump(merged_canonical_set, f)
            print(f"Tập hợp chuẩn hóa đã hợp nhất được lưu thành công tại '{output_canonical_set_file_path}'.")
        except Exception as e:
            print(f"Lỗi khi lưu tập hợp chuẩn hóa đã hợp nhất vào file '{output_canonical_set_file_path}': {e}")

    return merged_graph, merged_canonical_set

# --- Ví dụ sử dụng ---
if __name__ == "__main__":

    # Thực hiện hợp nhất
    merged_graph_result, merged_canonical_set_result = merge_knowledge_bases_from_pkl(
        graph_file_path1="/content/knowledge_graph_p3_0803.pkl",
        canonical_set_file_path1="/content/canonical_set_0803.pkl",
        graph_file_path2="/content/knowledge_graph_p3_9-10.pkl",
        canonical_set_file_path2="/content/canonical_set_9-10.pkl",
        output_graph_file_path="merged_knowledge_graph.pkl",
        output_canonical_set_file_path="merged_canonical_set.pkl"
    )

    print("\nKiểm tra đồ thị đã hợp nhất:")
    print(f"Nút trong đồ thị hợp nhất: {list(merged_graph_result.nodes(data=True))}")
    print(f"Cạnh trong đồ thị hợp nhất: {list(merged_graph_result.edges(data=True))}")

    print("\nKiểm tra tập hợp chuẩn hóa đã hợp nhất:")
    print(f"Các thực thể trong tập hợp chuẩn hóa: {merged_canonical_set_result}")

Đã tải đồ thị từ '/content/knowledge_graph_p3_0803.pkl' với 329 nút và 1653 cạnh.
Đã tải tập hợp chuẩn hóa từ '/content/canonical_set_0803.pkl' với 246 thực thể.
Đã tải đồ thị từ '/content/knowledge_graph_p3_9-10.pkl' với 132 nút và 391 cạnh.
Đã tải tập hợp chuẩn hóa từ '/content/canonical_set_9-10.pkl' với 87 thực thể.

Đồ thị đã hợp nhất có 423 nút và 2012 cạnh.
Tập hợp chuẩn hóa đã hợp nhất có 295 thực thể.
Đồ thị đã hợp nhất được lưu thành công tại 'merged_knowledge_graph.pkl'.
Tập hợp chuẩn hóa đã hợp nhất được lưu thành công tại 'merged_canonical_set.pkl'.

Kiểm tra đồ thị đã hợp nhất:
Nút trong đồ thị hợp nhất: [('Article_761: Châu Âu đối mặt "cơn ác mộng" khí đốt khi dự trữ giảm dưới 38% (thấp nhất 3 năm), phản đối nối lại Nord Stream 2, và tiến gần tịch thu 300 tỷ USD tài sản Nga', {'type': 'article', 'timestamp': Timestamp('2025-03-05 09:00:00+0000', tz='UTC')}), ('châu âu', {'type': 'entity', 'timestamp': Timestamp('2025-03-05 09:00:00+0000', tz='UTC')}), ('nga', {'type': 'e

In [ ]:
import networkx as nx
import pickle
import os

def merge_knowledge_bases_from_pkl(
    graph_file_path1: str,
    canonical_set_file_path1: str,
    graph_file_path2: str,
    canonical_set_file_path2: str,
    output_graph_file_path: str = None,
    output_canonical_set_file_path: str = None
) -> tuple[nx.DiGraph, set]:
    """
    Hợp nhất hai đồ thị NetworkX và hai tập hợp thực thể chuẩn hóa từ các file PKL.

    Parameters:
    - graph_file_path1 (str): Đường dẫn đến file PKL đồ thị thứ nhất.
    - canonical_set_file_path1 (str): Đường dẫn đến file PKL tập hợp chuẩn hóa thứ nhất.
    - graph_file_path2 (str): Đường dẫn đến file PKL đồ thị thứ hai.
    - canonical_set_file_path2 (str): Đường dẫn đến file PKL tập hợp chuẩn hóa thứ hai.
    - output_graph_file_path (str, optional): Đường dẫn để lưu đồ thị đã hợp nhất vào file PKL mới.
                                              Nếu None, đồ thị sẽ không được lưu.
    - output_canonical_set_file_path (str, optional): Đường dẫn để lưu tập hợp chuẩn hóa đã hợp nhất vào file PKL mới.
                                                        Nếu None, tập hợp chuẩn hóa sẽ không được lưu.

    Returns:
    - tuple[nx.DiGraph, set]: Một tuple chứa đồ thị đã hợp nhất và tập hợp chuẩn hóa đã hợp nhất.
    """
    graph1 = nx.DiGraph()
    graph2 = nx.DiGraph()
    canonical_set1 = set()
    canonical_set2 = set()

    # --- Tải Đồ thị 1 ---
    if os.path.exists(graph_file_path1):
        try:
            with open(graph_file_path1, 'rb') as f:
                graph1 = pickle.load(f)
            print(f"Đã tải đồ thị từ '{graph_file_path1}' với {graph1.number_of_nodes()} nút và {graph1.number_of_edges()} cạnh.")
        except Exception as e:
            print(f"Lỗi khi tải đồ thị từ '{graph_file_path1}': {e}")
            print(f"Sử dụng đồ thị rỗng cho '{graph_file_path1}'.")
    else:
        print(f"File '{graph_file_path1}' không tồn tại. Sử dụng đồ thị rỗng cho nó.")

    # --- Tải Canonical Set 1 ---
    if os.path.exists(canonical_set_file_path1):
        try:
            with open(canonical_set_file_path1, 'rb') as f:
                canonical_set1 = pickle.load(f)
            print(f"Đã tải tập hợp chuẩn hóa từ '{canonical_set_file_path1}' với {len(canonical_set1)} thực thể.")
        except Exception as e:
            print(f"Lỗi khi tải tập hợp chuẩn hóa từ '{canonical_set_file_path1}': {e}")
            print(f"Sử dụng tập hợp chuẩn hóa rỗng cho '{canonical_set_file_path1}'.")
    else:
        print(f"File '{canonical_set_file_path1}' không tồn tại. Sử dụng tập hợp chuẩn hóa rỗng cho nó.")

    # --- Tải Đồ thị 2 ---
    if os.path.exists(graph_file_path2):
        try:
            with open(graph_file_path2, 'rb') as f:
                graph2 = pickle.load(f)
            print(f"Đã tải đồ thị từ '{graph_file_path2}' với {graph2.number_of_nodes()} nút và {graph2.number_of_edges()} cạnh.")
        except Exception as e:
            print(f"Lỗi khi tải đồ thị từ '{graph_file_path2}': {e}")
            print(f"Sử dụng đồ thị rỗng cho '{graph_file_path2}'.")
    else:
        print(f"File '{graph_file_path2}' không tồn tại. Sử dụng đồ thị rỗng cho nó.")

    # --- Tải Canonical Set 2 ---
    if os.path.exists(canonical_set_file_path2):
        try:
            with open(canonical_set_file_path2, 'rb') as f:
                canonical_set2 = pickle.load(f)
            print(f"Đã tải tập hợp chuẩn hóa từ '{canonical_set_file_path2}' với {len(canonical_set2)} thực thể.")
        except Exception as e:
            print(f"Lỗi khi tải tập hợp chuẩn hóa từ '{canonical_set_file_path2}': {e}")
            print(f"Sử dụng tập hợp chuẩn hóa rỗng cho '{canonical_set_file_path2}'.")
    else:
        print(f"File '{canonical_set_file_path2}' không tồn tại. Sử dụng tập hợp chuẩn hóa rỗng cho nó.")

    # --- Hợp nhất hai đồ thị ---
    merged_graph = nx.DiGraph()
    merged_graph.add_nodes_from(graph1.nodes(data=True))
    merged_graph.add_edges_from(graph1.edges(data=True))
    merged_graph.add_nodes_from(graph2.nodes(data=True))
    merged_graph.add_edges_from(graph2.edges(data=True))

    print(f"\nĐồ thị đã hợp nhất có {merged_graph.number_of_nodes()} nút và {merged_graph.number_of_edges()} cạnh.")

    # --- Hợp nhất hai tập hợp chuẩn hóa ---
    merged_canonical_set = canonical_set1.union(canonical_set2)
    print(f"Tập hợp chuẩn hóa đã hợp nhất có {len(merged_canonical_set)} thực thể.")

    # --- Lưu đồ thị đã hợp nhất (nếu output_graph_file_path được cung cấp) ---
    if output_graph_file_path:
        output_graph_dir = os.path.dirname(output_graph_file_path)
        if output_graph_dir:
            os.makedirs(output_graph_dir, exist_ok=True)
        try:
            with open(output_graph_file_path, 'wb') as f:
                pickle.dump(merged_graph, f)
            print(f"Đồ thị đã hợp nhất được lưu thành công tại '{output_graph_file_path}'.")
        except Exception as e:
            print(f"Lỗi khi lưu đồ thị đã hợp nhất vào file '{output_graph_file_path}': {e}")

    # --- Lưu tập hợp chuẩn hóa đã hợp nhất (nếu output_canonical_set_file_path được cung cấp) ---
    if output_canonical_set_file_path:
        output_canonical_set_dir = os.path.dirname(output_canonical_set_file_path)
        if output_canonical_set_dir:
            os.makedirs(output_canonical_set_dir, exist_ok=True)
        try:
            with open(output_canonical_set_file_path, 'wb') as f:
                pickle.dump(merged_canonical_set, f)
            print(f"Tập hợp chuẩn hóa đã hợp nhất được lưu thành công tại '{output_canonical_set_file_path}'.")
        except Exception as e:
            print(f"Lỗi khi lưu tập hợp chuẩn hóa đã hợp nhất vào file '{output_canonical_set_file_path}': {e}")

    return merged_graph, merged_canonical_set

# --- Ví dụ sử dụng ---
if __name__ == "__main__":

    # Thực hiện hợp nhất
    merged_graph_result, merged_canonical_set_result = merge_knowledge_bases_from_pkl(
        graph_file_path1="/content/knowledge_graph_p3_checkpoint_0403_final.pkl",
        canonical_set_file_path1="/content/canonical_set_checkpoint_0403_final.pkl",
        graph_file_path2="/content/merged_knowledge_graph_0704_final.pkl",
        canonical_set_file_path2="/content/merged_canonical_set_0704_final.pkl",
        output_graph_file_path="merged_knowledge_graph_final.pkl",
        output_canonical_set_file_path="merged_canonical_set_final.pkl"
    )

    print("\nKiểm tra đồ thị đã hợp nhất:")
    print(f"Nút trong đồ thị hợp nhất: {list(merged_graph_result.nodes(data=True))}")
    print(f"Cạnh trong đồ thị hợp nhất: {list(merged_graph_result.edges(data=True))}")

    print("\nKiểm tra tập hợp chuẩn hóa đã hợp nhất:")
    print(f"Các thực thể trong tập hợp chuẩn hóa: {merged_canonical_set_result}")

Đã tải đồ thị từ '/content/knowledge_graph_p3_checkpoint_0403_final.pkl' với 1706 nút và 10442 cạnh.
Đã tải tập hợp chuẩn hóa từ '/content/canonical_set_checkpoint_0403_final.pkl' với 897 thực thể.
Đã tải đồ thị từ '/content/merged_knowledge_graph_0704_final.pkl' với 1801 nút và 10752 cạnh.
Đã tải tập hợp chuẩn hóa từ '/content/merged_canonical_set_0704_final.pkl' với 1065 thực thể.

Đồ thị đã hợp nhất có 3167 nút và 20272 cạnh.
Tập hợp chuẩn hóa đã hợp nhất có 1625 thực thể.
Đồ thị đã hợp nhất được lưu thành công tại 'merged_knowledge_graph_final.pkl'.
Tập hợp chuẩn hóa đã hợp nhất được lưu thành công tại 'merged_canonical_set_final.pkl'.

Kiểm tra đồ thị đã hợp nhất:
Nút trong đồ thị hợp nhất: [('Article_0: Thị trường CK 2025 kỳ vọng tăng trưởng sau Tết', {'type': 'article', 'timestamp': Timestamp('2025-02-01 09:00:00+0000', tz='UTC')}), ('vn - index', {'type': 'entity', 'timestamp': Timestamp('2025-03-09 09:00:00+0000', tz='UTC')}), ('nhóm ngân hàng', {'type': 'entity', 'timestamp':

In [ ]:
def filter_graph_by_date_range(G: nx.DiGraph, start_date: str | datetime | pd.Timestamp, end_date: str | datetime | pd.Timestamp) -> nx.DiGraph:
    """
    Lọc đồ thị để chỉ giữ lại các cạnh có dấu thời gian nằm trong khoảng [start_date, end_date].
    Đảm bảo tất cả dấu thời gian được chuẩn hóa thành múi giờ-naive (tz-naive) và chỉ phần ngày.

    Parameters:
    - G: Đồ thị NetworkX.
    - start_date: Ngày bắt đầu của khoảng lọc (bao gồm). Có thể là chuỗi, datetime, hoặc pd.Timestamp.
    - end_date: Ngày kết thúc của khoảng lọc (bao gồm). Có thể là chuỗi, datetime, hoặc pd.Timestamp.

    Returns:
    - Một bản sao của đồ thị đã lọc.
    """
    G_filtered = G.copy()

    # Chuyển đổi ngày bắt đầu và kết thúc sang pd.Timestamp, sau đó loại bỏ múi giờ
    # và chỉ lấy phần ngày (normalize về 00:00:00)
    try:
        start_ts = pd.to_datetime(start_date).normalize()
        end_ts = pd.to_datetime(end_date).normalize()
    except ValueError as e:
        print(f"Lỗi: Định dạng ngày bắt đầu hoặc ngày kết thúc không hợp lệ: {e}")
        return nx.DiGraph() # Trả về đồ thị rỗng nếu ngày không hợp lệ

    edges_to_remove = []
    for u, v, data in G_filtered.edges(data=True):
        edge_time = data.get("timestamp")

        if edge_time is None:
            # Loại bỏ các cạnh không có dấu thời gian nếu chúng ta đang lọc theo thời gian
            edges_to_remove.append((u, v))
            continue

        try:
            # Chuyển đổi dấu thời gian cạnh sang pd.Timestamp
            if isinstance(edge_time, pd.Timestamp):
                edge_ts = edge_time
            elif isinstance(edge_time, (int, float)):  # Dấu thời gian Unix
                edge_ts = pd.Timestamp(edge_time, unit='s')
            else:  # Thử phân tích cú pháp dưới dạng chuỗi
                edge_ts = pd.to_datetime(edge_time)

            # Chuẩn hóa dấu thời gian cạnh: loại bỏ múi giờ nếu có và chỉ lấy phần ngày
            if edge_ts.tz is not None:
                # Chuyển đổi sang múi giờ-naive. Lưu ý: có thể cần localize trước nếu muốn chuyển đổi múi giờ cụ thể.
                # Ở đây, chúng ta chỉ loại bỏ thông tin múi giờ, giữ nguyên thời điểm.
                edge_ts = edge_ts.tz_localize(None)
            edge_ts = edge_ts.normalize() # Đặt thời gian về 00:00:00 để chỉ so sánh ngày

            # Kiểm tra xem dấu thời gian cạnh có nằm trong khoảng không
            # edge_ts >= start_ts AND edge_ts <= end_ts
            if not (start_ts <= edge_ts <= end_ts):
                edges_to_remove.append((u, v))
        except Exception as e:
            # Bắt lỗi cụ thể 'TypeError' hoặc 'ValueError' nếu muốn chi tiết hơn
            print(f"Cảnh báo: Không thể xử lý dấu thời gian {edge_time} cho cạnh ({u}, {v}) khi lọc: {e}")
            edges_to_remove.append((u, v)) # Loại bỏ các cạnh có dấu thời gian lỗi
            continue

    # Xóa các cạnh không nằm trong khoảng
    for u, v in edges_to_remove:
        if G_filtered.has_edge(u, v):
            G_filtered.remove_edge(u, v)

    print(f"Đã lọc: Loại bỏ {len(edges_to_remove)} cạnh không nằm trong khoảng từ {start_ts.date().isoformat()} đến {end_ts.date().isoformat()}.")
    return G_filtered

In [ ]:
import networkx as nx
import pandas as pd
from datetime import datetime, timedelta
import pickle
import os # Dùng để kiểm tra và xóa file dummy nếu cần

def graph_to_tuples(G):
    """
    Chuyển đổi đồ thị thành một chuỗi các tuple (ngày, nguồn, tác động, đích).
    """
    tuples = []
    for u, v, data in G.edges(data=True):
        # Trích xuất ngày dưới dạng chuỗi, xử lý các định dạng dấu thời gian khác nhau
        timestamp = data.get("timestamp")
        if timestamp is None:
            # Bỏ qua các cạnh không có dấu thời gian
            continue

        try:
            # Xử lý các định dạng dấu thời gian khác nhau
            if isinstance(timestamp, pd.Timestamp):
                date_str = timestamp.date().isoformat()
            elif hasattr(timestamp, "date"):  # đối tượng datetime
                date_str = timestamp.date().isoformat()
            elif isinstance(timestamp, (int, float)):  # Dấu thời gian Unix
                # Chắc chắn rằng đây là miligiây hoặc giây tùy thuộc vào dữ liệu của bạn.
                # Mặc định ở đây là giây. Nếu là miligiây, hãy dùng unit='ms'
                date_str = pd.Timestamp(timestamp, unit='s').date().isoformat()
            else:  # Thử phân tích cú pháp dưới dạng chuỗi
                parsed_date = pd.to_datetime(timestamp)
                date_str = parsed_date.date().isoformat()

            # Bỏ qua các thực thể không hợp lệ trong các tuple đầu ra
            if "không có thực thể nào" in str(u).lower() or "không có thực thể nào" in str(v).lower():
                continue

            tuples.append(f"({date_str}, {u}, {data.get('impact')} TO, {v})")
        except Exception as e:
            print(f"Lỗi khi xử lý cạnh ({u}, {v}): {e}, dấu thời gian: {timestamp}, loại: {type(timestamp)}")
            continue

    # Sắp xếp các tuple theo thứ tự tăng dần của ngày
    # Giả sử định dạng ngày là ISO (YYYY-MM-DD) để có thể sắp xếp chuỗi
    return "\n".join(sorted(tuples))

In [ ]:
graph_file = "/content/merged_knowledge_graph_0704_updated.pkl"
try:
    with open(graph_file, 'rb') as f:
        G = pickle.load(f)
    print(f"Đã tải đồ thị từ '{graph_file}'.")
except FileNotFoundError:
    print(f"Lỗi: Không tìm thấy file đồ thị '{graph_file}'. Vui lòng đảm bảo file tồn tại.")
    exit()
except Exception as e:
    print(f"Lỗi khi tải đồ thị: {e}")
    exit()

# --- Định nghĩa khoảng thời gian để lọc ---
#Lọc các cạnh trong một ngày cụ thể (2025-02-02)
start_filter_date_1 = "2025-03-31"
end_filter_date_1 = "2025-03-31"
print(f"\n--- Lọc các cạnh trong khoảng ngày: {start_filter_date_1} đến {end_filter_date_1} ---")
G_filtered_1 = filter_graph_by_date_range(G, start_filter_date_1, end_filter_date_1)
print(f"Số cạnh còn lại sau khi lọc theo 1 ngày: {G_filtered_1.number_of_edges()}")
print("\nKết quả các tuple đã lọc (theo 1 ngày):")
result_tuples_1 = graph_to_tuples(G_filtered_1)
print(result_tuples_1)
# export_tuples_to_txt(result_tuples_1, "filtered_tuples_2025_03_16.txt")

Đã tải đồ thị từ '/content/merged_knowledge_graph_0704_updated.pkl'.

--- Lọc các cạnh trong khoảng ngày: 2025-03-31 đến 2025-03-31 ---
Đã lọc: Loại bỏ 10493 cạnh không nằm trong khoảng từ 2025-03-31 đến 2025-03-31.
Số cạnh còn lại sau khi lọc theo 1 ngày: 259

Kết quả các tuple đã lọc (theo 1 ngày):
(2025-03-31, Article_1284: Lãi suất huy động tiếp tục giảm, lợi nhuận ngân hàng tăng trưởng, POSITIVE TO, agribank)
(2025-03-31, Article_1284: Lãi suất huy động tiếp tục giảm, lợi nhuận ngân hàng tăng trưởng, POSITIVE TO, lpbank)
(2025-03-31, Article_1284: Lãi suất huy động tiếp tục giảm, lợi nhuận ngân hàng tăng trưởng, POSITIVE TO, nhnn)
(2025-03-31, Article_1284: Lãi suất huy động tiếp tục giảm, lợi nhuận ngân hàng tăng trưởng, POSITIVE TO, vpbank)
(2025-03-31, Article_1285: Sốt đất vùng ven, đấu giá sôi động và đề xuất giải pháp nhà ở, POSITIVE TO, hà nội)
(2025-03-31, Article_1285: Sốt đất vùng ven, đấu giá sôi động và đề xuất giải pháp nhà ở, POSITIVE TO, hưng yên)
(2025-03-31, Artic

In [ ]:
import pandas as pd
import networkx as nx
import pickle
import os
import re

def update_article_node_names(graph_input_path, articles_csv_path, graph_output_path):
    """
    Tải đồ thị từ file đầu vào, tìm các nút bài báo chỉ có 'Article_postID',
    sau đó bổ sung tiêu đề từ file CSV và lưu đồ thị đã sửa đổi vào một file mới.

    Args:
        graph_input_path (str): Đường dẫn đến file .pkl của đồ thị gốc.
        articles_csv_path (str): Đường dẫn đến file CSV chứa thông tin bài báo.
        graph_output_path (str): Đường dẫn để lưu file .pkl của đồ thị đã sửa đổi.
    """
    # 1. Tải đồ thị hiện có
    G = nx.DiGraph()
    if os.path.exists(graph_input_path):
        try:
            with open(graph_input_path, "rb") as f:
                G = pickle.load(f)
            print(f"Đã tải đồ thị gốc từ '{graph_input_path}' với {G.number_of_nodes()} nút và {G.number_of_edges()} cạnh.")
        except Exception as e:
            print(f"Lỗi khi tải đồ thị từ '{graph_input_path}': {e}. Vui lòng kiểm tra file. Thoát chương trình.")
            return
    else:
        print(f"Lỗi: File đồ thị gốc '{graph_input_path}' không tồn tại. Không có đồ thị để sửa đổi.")
        return

    # 2. Tải DataFrame chứa thông tin bài báo
    try:
        df_articles = pd.read_csv(articles_csv_path)
        if 'postID' in df_articles.columns:
            df_articles['postID'] = df_articles['postID'].astype(int)
        print("Đã tải file CSV bài báo thành công.")
    except FileNotFoundError:
        print(f"Lỗi: Không tìm thấy file '{articles_csv_path}'. Vui lòng kiểm tra đường dẫn. Thoát chương trình.")
        return
    except Exception as e:
        print(f"Lỗi khi đọc file CSV bài báo: {e}. Thoát chương trình.")
        return

    # Tạo một dictionary để tra cứu tiêu đề nhanh chóng theo postID
    article_titles = df_articles.set_index('postID')['title'].to_dict()

    # 3. Chuẩn bị đổi tên các nút
    nodes_to_rename = {}
    # Biểu thức chính quy để khớp với "Article_postID" mà KHÔNG CÓ tiêu đề đính kèm
    article_node_pattern = re.compile(r"^Article_(\d+)$")

    print("Đang quét các nút trong đồ thị để tìm các nút bài báo cần cập nhật...")
    for node_name in list(G.nodes()): # Lặp qua một bản sao của các nút
        match = article_node_pattern.match(node_name)
        if match:
            post_id = int(match.group(1))

            if post_id in article_titles:
                title = article_titles[post_id]
                new_node_name = f"Article_{post_id}: {title}"
                # Chỉ thêm vào danh sách đổi tên nếu tên mới khác tên cũ
                if node_name != new_node_name:
                    nodes_to_rename[node_name] = new_node_name
            else:
                print(f"Cảnh báo: Không tìm thấy tiêu đề cho postID {post_id} (nút: '{node_name}') trong file CSV.")

    print(f"Tìm thấy {len(nodes_to_rename)} nút bài báo cần được đổi tên.")

    # 4. Đổi tên các nút trong đồ thị
    if nodes_to_rename:
        # Sử dụng nx.relabel_nodes để đổi tên hiệu quả, giữ nguyên các cạnh và thuộc tính
        # copy=False để sửa đổi đồ thị trực tiếp
        G = nx.relabel_nodes(G, nodes_to_rename, copy=False)
        print("Đã đổi tên các nút bài báo thành công.")
    else:
        print("Không có nút bài báo nào cần đổi tên theo tiêu chí đã đặt.")

    # 5. Lưu đồ thị đã sửa đổi vào file mới
    try:
        # Đảm bảo thư mục đầu ra tồn tại
        output_dir = os.path.dirname(graph_output_path)
        if output_dir:
            os.makedirs(output_dir, exist_ok=True)

        with open(graph_output_path, "wb") as f:
            pickle.dump(G, f)
        print(f"Đồ thị đã sửa đổi (bao gồm tiêu đề bài báo) đã được lưu vào file mới: '{graph_output_path}'.")
        print(f"Tổng số nút trong đồ thị đã sửa đổi: {G.number_of_nodes()}, Tổng số cạnh: {G.number_of_edges()}.")
    except Exception as e:
        print(f"Lỗi khi lưu đồ thị đã sửa đổi vào file '{graph_output_path}': {e}")

# --- Sử dụng hàm ---
if __name__ == "__main__":
    # Thay đổi đường dẫn file nếu cần thiết
    original_graph_file = "/content/merged_knowledge_graph_0704.pkl"
    articles_data_csv = "/content/summarized_articles.csv"
    # Đường dẫn đến file mới để lưu đồ thị đã sửa đổi
    updated_graph_file = "/content/merged_knowledge_graph_0704_updated.pkl"

    # Gọi hàm để bắt đầu quá trình cập nhật
    update_article_node_names(original_graph_file, articles_data_csv, updated_graph_file)

Đã tải đồ thị gốc từ '/content/merged_knowledge_graph_0704.pkl' với 1801 nút và 10752 cạnh.
Đã tải file CSV bài báo thành công.
Đang quét các nút trong đồ thị để tìm các nút bài báo cần cập nhật...
Tìm thấy 25 nút bài báo cần được đổi tên.
Đã đổi tên các nút bài báo thành công.
Đồ thị đã sửa đổi (bao gồm tiêu đề bài báo) đã được lưu vào file mới: '/content/merged_knowledge_graph_0704_updated.pkl'.
Tổng số nút trong đồ thị đã sửa đổi: 1801, Tổng số cạnh: 10752.


In [ ]:
import networkx as nx
import pickle
import os

def extract_and_save_canonical_set(graph_path, output_canonical_set_path):
    """
    Tải đồ thị, trích xuất tất cả các thực thể và nút cổ phiếu,
    sau đó lưu chúng vào một file canonical set mới.

    Args:
        graph_path (str): Đường dẫn đến file .pkl của đồ thị.
        output_canonical_set_path (str): Đường dẫn để lưu file .pkl của canonical set.
    """
    # 1. Tải đồ thị hiện có
    G = nx.DiGraph()
    if os.path.exists(graph_path):
        try:
            with open(graph_path, "rb") as f:
                G = pickle.load(f)
            print(f"Đã tải đồ thị từ '{graph_path}' với {G.number_of_nodes()} nút và {G.number_of_edges()} cạnh.")
        except Exception as e:
            print(f"Lỗi khi tải đồ thị từ '{graph_path}': {e}. Vui lòng kiểm tra file. Thoát chương trình.")
            return
    else:
        print(f"Lỗi: File đồ thị '{graph_path}' không tồn tại. Không thể trích xuất canonical set.")
        return

    # 2. Trích xuất các thực thể và cổ phiếu vào canonical set
    canonical_entities = set()
    print("Đang trích xuất các thực thể từ đồ thị...")
    for node, data in G.nodes(data=True):
        node_type = data.get('type')
        # Thêm nút vào canonical_entities nếu nó là 'entity' hoặc 'stock'
        # và không phải là nút bài báo (để tránh nhầm lẫn)
        if node_type in ["entity", "stock"] and not str(node).startswith("Article_"):
            canonical_entities.add(node)
        # Bổ sung: nếu nút bài báo có đính kèm tiêu đề, hãy thử trích xuất các thực thể từ đó
        # Đây là một biện pháp an toàn nếu có lỗi trong quá trình ban đầu không thêm đúng cách
        elif node_type == "article" and ":" in str(node):
            # Ví dụ: "Article_716: Việt Nam xếp thứ 2..."
            # Phần này sẽ không được thêm vào canonical_set vì nó là "Article"
            # Nhưng nếu có lỗi logic trước đó và "Article_..." lại là một thực thể,
            # thì bạn cần điều chỉnh điều kiện trên.
            pass # Nút bài báo không nên là một thực thể trong canonical_set

    print(f"Đã trích xuất {len(canonical_entities)} thực thể duy nhất.")

    # 3. Lưu canonical set vào file mới
    try:
        # Đảm bảo thư mục đầu ra tồn tại
        output_dir = os.path.dirname(output_canonical_set_path)
        if output_dir:
            os.makedirs(output_dir, exist_ok=True)

        with open(output_canonical_set_path, "wb") as f:
            pickle.dump(canonical_entities, f)
        print(f"Canonical set đã được lưu thành công vào '{output_canonical_set_path}'.")
    except Exception as e:
        print(f"Lỗi khi lưu canonical set vào file '{output_canonical_set_path}': {e}")

# --- Sử dụng hàm ---
if __name__ == "__main__":
    # Đường dẫn đến file đồ thị .pkl của bạn
    graph_input_path = "/content/merged_knowledge_graph_0704_final.pkl" # Sử dụng file đã cập nhật tên nút nếu bạn đã chạy bước trước đó

    # Đường dẫn đến file canonical set mới mà bạn muốn tạo
    output_canonical_set_path = "/content/merged_canonical_set_0704_final.pkl"

    # Gọi hàm để trích xuất và lưu canonical set
    extract_and_save_canonical_set(graph_input_path, output_canonical_set_path)

Đã tải đồ thị từ '/content/merged_knowledge_graph_0704_final.pkl' với 1801 nút và 10752 cạnh.
Đang trích xuất các thực thể từ đồ thị...
Đã trích xuất 1065 thực thể duy nhất.
Canonical set đã được lưu thành công vào '/content/merged_canonical_set_0704_final.pkl'.


In [ ]:
import pickle
import os

def count_entities_in_canonical_set(canonical_set_path):
    """
    Tải canonical set từ file .pkl và đếm số lượng thực thể bên trong.

    Args:
        canonical_set_path (str): Đường dẫn đến file .pkl của canonical set.
    """
    if not os.path.exists(canonical_set_path):
        print(f"Lỗi: File canonical set '{canonical_set_path}' không tồn tại.")
        return

    try:
        with open(canonical_set_path, "rb") as f:
            canonical_entities = pickle.load(f)

        if isinstance(canonical_entities, set):
            num_entities = len(canonical_entities)
            print(f"Đã tìm thấy {num_entities} thực thể trong file '{canonical_set_path}'.")
        else:
            print(f"Lỗi: Nội dung của file '{canonical_set_path}' không phải là một tập hợp (set).")

    except Exception as e:
        print(f"Lỗi khi tải hoặc xử lý file canonical set '{canonical_set_path}': {e}")

# --- Sử dụng hàm ---
if __name__ == "__main__":
    # Thay đổi đường dẫn file canonical set của bạn tại đây
    canonical_set_file = "/content/merged_canonical_set_0704_updated.pkl"

    # Gọi hàm để đếm thực thể
    count_entities_in_canonical_set(canonical_set_file)

Đã tìm thấy 1065 thực thể trong file '/content/merged_canonical_set_0704_updated.pkl'.
